In [1]:
import pandas as pd
import os
import subprocess
from Bio.PDB import PDBParser
from Bio.PDB import Model
import sys
import numpy as np
import re
from Bio.Data import IUPACData
import shutil
from pathlib import PosixPath

In [2]:
protein_letters_3to1 = {value:key for key,value in IUPACData.protein_letters_1to3.items()}
protein_letters_1to3 = {key:value for key,value in IUPACData.protein_letters_1to3.items()}

In [3]:
!pwd

/ibex/scratch/penaguka/VAP/thesis


In [6]:
gnomad_expanded = pd.read_pickle('/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/gnomad_expanded.pkl')

In [7]:
pd.set_option('display.width', None)
pd.set_option('display.max_columns', None) 

In [8]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.min_rows', 50)

In [8]:
gnomad_expanded['prot_length'].nlargest(50)

5793    8797
5794    8797
5795    8797
5796    8797
5797    8797
5798    8797
5799    8797
5800    8797
5801    8797
5802    8797
5803    8797
5804    8797
5805    8797
5806    8797
2536    8525
2537    8525
2538    8525
2539    8525
2540    8525
2541    8525
2542    8525
2543    8525
2544    8525
2545    8525
2546    8525
2547    8525
2548    8525
2549    8525
2550    8525
2551    8525
1805    6907
1806    6907
1807    6907
1808    6907
1809    6907
1810    6907
1811    6907
1812    6907
1813    6907
1814    6907
1815    6907
1816    6907
1817    6907
1818    6907
1819    6907
1820    6907
1821    6907
1822    6907
1823    6907
1824    6907
Name: prot_length, dtype: int64

In [68]:
top_rows = gnomad_expanded.nlargest(50, 'prot_length')

In [69]:
top_rows

#CHROM        POS          ID REF ALT      AC         AF      AN     QD  \
5793   chr6  152122609   rs2295190   G   T   28800   0.114579  251356  15.08   
5794   chr6  152122626   rs2295192   C   T   12978  0.0516426  251304  14.11   
5795   chr6  152132156  rs35591210   G   A   12818  0.0509674  251494  12.92   
5796   chr6  152148053   rs2252755   C   G   90595   0.364201  248750  15.81   
5797   chr6  152149617  rs17082236   C   A   16253  0.0646366  251452  12.83   
5798   chr6  152219143   rs2147377   A   C  249278   0.991914  251310  34.12   
5799   chr6  152326546   rs2306916   A   T  196687   0.782392  251392  27.31   
5800   chr6  152330899   rs6911096   A   T  195948   0.779557  251358  26.44   
5801   chr6  152337006  rs28385621   C   A   18754  0.0748364  250600  15.13   
5802   chr6  152337007   rs9479297   T   C  187478   0.749348  250188  27.23   
5803   chr6  152344126   rs4645434   C   A  146655   0.583219  251458  20.79   
5804   chr6  152387175    rs214950   G   A   59044   0.235237  250998  16.13   
5805   chr6  152451129    rs214976   A   G  117956   0.469159  251420  21.56   
5806   chr6  152455960  rs17082709   A   C   13784  0.0548342  251376  13.51   
2536   chr2  151619514  rs10172023   C   G   72637   0.292241  248552  18.67   
2537   chr2  151619514  rs10172023   C   G   72637   0.292241  248552  18.67   
2538   chr2  151640012   rs6713162   A   G   60525   0.243059  249014  16.62   
2539   chr2  151640012   rs6713162   A   G   60525   0.243059  249014  16.62   
2540   chr2  151643935  rs13013209   C   G  104730   0.420181  249250  20.12   
2541   chr2  151643935  rs13013209   C   G  104730   0.420181  249250  20.12   
2542   chr2  151659169  rs75807392   G   A   19116   0.077174  247700  14.19   
2543   chr2  151659169  rs75807392   G   A   19116   0.077174  247700  14.19   
2544   chr2  151671058   rs7426114   C   T  187196   0.751103  249228  27.16   
2545   chr2  151671058   rs7426114   C   T  187196   0.751103  249228  27.16   
2546   chr2  151671094  rs34577613   C   T   45602   0.182958  249248  15.28   
2547   chr2  151671094  rs34577613   C   T   45602   0.182958  249248  15.28   
2548   chr2  151674563   rs6711382   A   G  207597   0.833502  249066  29.16   
2549   chr2  151674563   rs6711382   A   G  207597   0.833502  249066  29.16   
2550   chr2  151679984   rs6735208   T   A  189525   0.760949  249064  25.88   
2551   chr2  151679984   rs6735208   T   A  189525   0.760949  249064  25.88   
1805   chr2  185763216  rs17228441   T   C   74333   0.545211  136338  20.27   
1806   chr2  185789865    rs992822   A   G   73887   0.545388  135476  23.11   
1807   chr2  185790140  rs79762465   G   C   17493   0.129361  135226  15.28   
1808   chr2  185790999  rs10931199   G   A  128399   0.972808  131988  33.99   
1809   chr2  185792229  rs17229201   T   C   74069   0.544489  136034   20.1   
1810   chr2  185793329  rs60029104   G   A   73458    0.54139  135684  20.79   
1811   chr2  185793711  rs10490391   C   T   74938   0.544544  137616  21.59   
1812   chr2  185793838  rs10490392   G   T   72323   0.543725  133014  20.87   
1813   chr2  185794457  rs77937204   C   A    8888  0.0772708  115024  14.28   
1814   chr2  185794632   rs2161036   G   T   73385   0.544949  134664  21.83   
1815   chr2  185796840  rs12999160   G   A    8412  0.0615641  136638   13.7   
1816   chr2  185800236  rs10931200   C   A   73860   0.544867  135556  21.74   
1817   chr2  185800705  rs36004074   G   A   74312   0.545025  136346  21.95   
1818   chr2  185801097  rs11695215   A   G   72980   0.545449  133798  22.55   
1819   chr2  185802394   rs7605884   T   C   73752   0.546959  134840  23.21   
1820   chr2  185802633   rs7565527   A   C   12614   0.092821  135896  14.13   
1821   chr2  185803987  rs17826419   A   T    7220  0.0643459  112206  15.55   
1822   chr2  185804208  rs13003744   A   G   42096   0.338894  124216  17.75   
1823   chr2  185805377   rs7576532   A   C  228596   0.972633  235028  34.24   
1824 

In [11]:
gnomad_expanded['PDB_path'].loc[9605]

PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q92832-F1-model_v4.pdb')

In [12]:
for path in gnomad_expanded['PDB_path']:
    print(path)

/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q8NBI3-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P42898-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P51797-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P01160-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q02809-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q02809-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q5JXC2-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q5JXC2-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q5JXC2-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P20333-F1-model_v4.pdb
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_human_v4/AF-Q5THJ4-F5-model_v4.pdb
/ibex/

In [7]:
gnomad_expanded

#CHROM       POS            ID REF ALT      AC         AF      AN  \
0       chr1  11706367    rs11121804   C   T   39444   0.158732  248494   
1       chr1  11790870     rs2274976   C   T   13949  0.0555184  251250   
2       chr1  11824498      rs198400   A   G  250947   0.999399  251098   
3       chr1  11847591        rs5063   C   T   14048  0.0558586  251492   
4       chr1  11949899     rs7551175   G   A   45490   0.180978  251356   
5       chr1  11950412     rs2273285   G   T   21778  0.0866876  251224   
6       chr1  12022277    rs11553925   A   T   49896   0.199681  249878   
7       chr1  12022404    rs11588712   C   T   27588   0.119221  231402   
8       chr1  12022869     rs2295283   A   G  165360   0.682133  242416   
9       chr1  12192898     rs1061622   T   G   54148   0.216294  250344   
10      chr1  12279562     rs4845898   A   T   55150   0.219676  251052   
11      chr1  12725782    rs11121969   C   T   14579  0.0584929  249244   
12      chr1  12794279     rs1769774   C   T   77773   0.310838  250204   
13      chr1  12795729     rs1052908   A   C   50855   0.268197  189618   
14      chr1  12828511   rs200394590   T   G   28573   0.212483  134472   
15      chr1  12847526    rs74055698   T   C   40607   0.176483  230090   
16      chr1  12847643   rs138700801   T   C   12357  0.0503603  245372   
17      chr1  12847680   rs141872266   T   C   13186   0.053552  246228   
18      chr1  12859108     rs9661554   G   T   26002    0.10414  249682   
19      chr1  12859209     rs3204790   T   G   40973    0.16561  247406   
20      chr1  12859224     rs9659529   C   G   26417   0.105534  250318   
21      chr1  12859226    rs45443899   C   T   26237   0.104801  250350   
22      chr1  12859769    rs80027487   C   G   25356   0.101816  249038   
23      chr1  12860017     rs3204798   T   G   14546  0.0586551  247992   
24      chr1  12860073    rs72472698   A   G   26776   0.107356  249414   
...      ...       ...           ...  ..  ..     ...        ...     ...   
15916   chrX  50376086     rs4074320   C   T   41414   0.231714  178729   
15917   chrX  50911091    rs41308602   A   G    7747  0.0570719  135741   
15918   chrX  52645464   rs112382781   G   T   16845  0.0979064  172052   
15919   chrX  54755097    rs17316491   C   G   11594  0.0642555  180436   
15920   chrX  54925031    rs45448595   C   T   10765  0.0596419  180494   
15921   chrX  55090033     rs1845444   C   G  177865   0.979125  181657   
15922   chrX  55263341     rs4826381   T   C  169359   0.933792  181367   
15923   chrX  55624568     rs2375465   T   C  170097   0.934383  182042   
15924   chrX  57136462     rs2003812   G   A   41123    0.93108   44167   
15925   chrX  57592412   rs199513692   G   A    4161   0.050147   82976   
15926   chrX  57592416   rs200267267   A   C    4385  0.0567322   77293   
15927   chrX  57592437   rs189164178   G   A   10971   0.168288   65192   
15928   chrX  66602765     rs1385698   T   C  149078   0.980931  151976   
15929   chrX  66605144     rs1385699   C   T  140733   0.793474  177363   
15930   chrX  68432906    rs41303733   C   T   10488  0.0572795  183102   
15931   chrX  69505797     rs1171942   T   C   89348   0.492984  181239   
15932   chrX  70258925     rs3829709   A   C   20562   0.114082  180239   
15933   chrX  70259092     rs1152187   T   G   42510   0.232866  182551   
15934   chrX  70341930     rs1199457   T   G   10828  0.0613596  176468   
15935   chrX  70926625     rs6525447   G   C   36218   0.238416  151911   
15936   chrX  72140250     rs7061150   C   T   12196  0.0674621  180783   
15937   chrY   6246522   rs201475959   A   G    1025  0.0780952   13125   
15938   chrY  12720687     rs7067496   G   T    6033  0.0894759   67426   
15939   chrY  22180292  rs1478920645   G   T       1   0.142857       7   
15940   chrY  22406127  rs1195699969   C   A       9          1       9   

          QD variant_type                                                vep  \
0      13.47        mixed

In [8]:
gnomad_expanded['PDB_path'].value_counts()

/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-B1PKY1-F1-model_v4.pdb         59
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-E5FQ95-F1-model_v4.pdb         53
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P10321-F1-model_v4.pdb         51
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q5Y7D6-F1-model_v4.pdb         47
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-D7RIH8-F1-model_v4.pdb         36
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-A0A2Z4LKS3-F1-model_v4.pdb     34
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-A0A173ADG5-F1-model_v4.pdb     30
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-E2RYF6-F1-model_v4.pdb         29
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P20231-F1-model_v4.pdb         23
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-I4EC15-F1-model_v4.pdb  

In [28]:
for item in gnomad_expanded['PDB_path'].unique():
    path = item
    for index, row in gnomad_expanded[gnomad_expanded['PDB_path'] == path].iterrows():
    # Access the row data using row['column_name'] or row[column_index]
    # modify the row values directly
    # For example, update a specific column value
    gnomad_expanded.at[index, 'column_name'] = new_value

<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q8NBI3-F1-model_v4.pdb
<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P42898-F1-model_v4.pdb
<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P51797-F1-model_v4.pdb
<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P01160-F1-model_v4.pdb
<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q02809-F1-model_v4.pdb
<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q5JXC2-F1-model_v4.pdb
<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P20333-F1-model_v4.pdb
<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_human_v4/AF-Q5THJ4-F5-model_v4.pdb
<class 'pathlib.PosixPath'>
/ibex/scratch/projects/c

In [9]:
pdb_paths = gnomad_expanded['PDB_path'].unique()

In [24]:
path = gnomad_expanded['PDB_path'].unique()
path

array([PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q8NBI3-F1-model_v4.pdb'),
       PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P42898-F1-model_v4.pdb'),
       PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P51797-F1-model_v4.pdb'),
       ...,
       PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-A6NKD2-F1-model_v4.pdb'),
       PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-O00507-F1-model_v4.pdb'),
       PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q15415-F1-model_v4.pdb')],
      dtype=object)

In [ ]:
temp_df = gnomad_expanded[gnomad_expanded['PDB_path'] == path].copy()

In [43]:
temp_df = gnomad_expanded[gnomad_expanded['PDB_path'] == PosixPath('/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-B1PKY1-F1-model_v4.pdb')].copy()

In [15]:
len(pdb_paths)

7698

In [10]:
paths = [str(x).split("/")[-1].split(".")[0] for x in pdb_paths]

In [27]:
len(paths)

7698

In [19]:
# Path to the output folder
output_folder = '/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad'

In [13]:
already_done = pd.read_pickle('/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/clinvar_raptorx.pkl')

In [12]:
!pwd

/ibex/scratch/penaguka/VAP/thesis


In [14]:
already_done

['AF-P82279-F1-model_v4',
 'AF-P08575-F1-model_v4',
 'AF-Q15058-F1-model_v4',
 'AF-Q5T1V6-F1-model_v4',
 'AF-Q11203-F1-model_v4',
 'AF-Q5VTB9-F1-model_v4',
 'AF-Q9NR50-F1-model_v4',
 'AF-P06132-F1-model_v4',
 'AF-Q96IR7-F1-model_v4',
 'AF-P56696-F1-model_v4',
 'AF-Q9HAB8-F1-model_v4',
 'AF-Q8N6F1-F1-model_v4',
 'AF-Q32P28-F1-model_v4',
 'AF-P11166-F1-model_v4',
 'AF-P30613-F1-model_v4',
 'AF-P14324-F1-model_v4',
 'AF-Q9NR48-F5-model_v4',
 'AF-Q9NR48-F1-model_v4',
 'AF-Q9BUK6-F1-model_v4',
 'AF-Q92963-F1-model_v4',
 'AF-A0A384MQX1-F1-model_v4',
 'AF-Q15392-F1-model_v4',
 'AF-Q5VU50-F1-model_v4',
 'AF-Q8NBP7-F1-model_v4',
 'AF-Q9H2M9-F1-model_v4',
 'AF-Q9NVF7-F1-model_v4',
 'AF-A0A024R3P1-F1-model_v4',
 'AF-A0A499FIZ0-F1-model_v4',
 'AF-Q14739-F1-model_v4',
 'AF-A1NY77-F1-model_v4',
 'AF-A0A0S2Z5U6-F1-model_v4',
 'AF-P98160-F14-model_v4',
 'AF-P98160-F5-model_v4',
 'AF-O75445-F14-model_v4',
 'AF-O75445-F13-model_v4',
 'AF-O75445-F12-model_v4',
 'AF-O75445-F10-model_v4',
 'AF-O75445-F9-mo

In [21]:
# Obtener los elementos en lista1 pero no en lista2
diferencia1 = set(already_done) - set(paths)

# Obtener los elementos en lista2 pero no en lista1
diferencia2 = set(paths) - set(already_done)

# Imprimir los resultados
#print("Elementos en already_done pero no en paths:", diferencia1)
print("Elementos en paths pero no en already_done:", diferencia2)

Elementos en paths pero no en already_done: {'AF-P07288-F1-model_v4', 'AF-Q8TE73-F10-model_v4', 'AF-Q6NT89-F1-model_v4', 'AF-A0A804HL01-F1-model_v4', 'AF-A0A140VJD4-F1-model_v4', 'AF-P54296-F1-model_v4', 'AF-Q07283-F1-model_v4', 'AF-Q96JA1-F1-model_v4', 'AF-Q96JB2-F1-model_v4', 'AF-A0A024RBE2-F1-model_v4', 'AF-P0C7Q2-F1-model_v4', 'AF-E9PQR5-F1-model_v4', 'AF-Q5W041-F1-model_v4', 'AF-P0C7P0-F1-model_v4', 'AF-Q8NH53-F1-model_v4', 'AF-Q8TDY2-F1-model_v4', 'AF-H3BV12-F1-model_v4', 'AF-O14975-F1-model_v4', 'AF-Q96R09-F1-model_v4', 'AF-Q8N0V3-F1-model_v4', 'AF-Q7Z570-F1-model_v4', 'AF-Q9NZP8-F1-model_v4', 'AF-D6RA61-F1-model_v4', 'AF-P0C7H8-F1-model_v4', 'AF-A6NIR3-F1-model_v4', 'AF-O14717-F1-model_v4', 'AF-Q9NYA3-F1-model_v4', 'AF-P0DJJ0-F1-model_v4', 'AF-Q9NTJ3-F1-model_v4', 'AF-A0A2Z4LIS9-F1-model_v4', 'AF-A0A3B3ISU3-F1-model_v4', 'AF-Q5JU69-F1-model_v4', 'AF-Q9UHE5-F1-model_v4', 'AF-P28676-F1-model_v4', 'AF-Q6N043-F1-model_v4', 'AF-Q8NEM2-F1-model_v4', 'AF-Q9Y5G5-F1-model_v4', 'AF-Q9Y4D

In [22]:
new_paths = list(diferencia2)

In [30]:
new_paths

['AF-Q9NXL9-F1-model_v4',
 'AF-Q9ULM3-F1-model_v4',
 'AF-P60371-F1-model_v4',
 'AF-Q9NUL3-F1-model_v4',
 'AF-Q9NUJ7-F1-model_v4',
 'AF-Q86W24-F1-model_v4',
 'AF-Q96QC4-F1-model_v4',
 'AF-Q16204-F1-model_v4',
 'AF-Q8IXR9-F1-model_v4',
 'AF-Q6NUN0-F1-model_v4',
 'AF-A0A0C4DG52-F1-model_v4',
 'AF-Q7Z3Y8-F1-model_v4',
 'AF-P59533-F1-model_v4',
 'AF-Q70CQ2-F1-model_v4',
 'AF-Q9BVS4-F1-model_v4',
 'AF-A0A090N8Y3-F1-model_v4',
 'AF-O75417-F1-model_v4',
 'AF-Q92569-F1-model_v4',
 'AF-Q15937-F1-model_v4',
 'AF-Q6ZW31-F1-model_v4',
 'AF-Q6XPS3-F1-model_v4',
 'AF-A0A0C4DG85-F1-model_v4',
 'AF-Q8WXH0-F12-model_v4',
 'AF-Q92954-F1-model_v4',
 'AF-Q86TB3-F1-model_v4',
 'AF-P43363-F1-model_v4',
 'AF-E7ERA6-F1-model_v4',
 'AF-Q8N699-F1-model_v4',
 'AF-P22792-F1-model_v4',
 'AF-A0A140VJI5-F1-model_v4',
 'AF-Q8TCG2-F1-model_v4',
 'AF-P31997-F1-model_v4',
 'AF-Q9Y2L5-F1-model_v4',
 'AF-A7MBM2-F1-model_v4',
 'AF-Q86TC9-F1-model_v4',
 'AF-P49223-F1-model_v4',
 'AF-Q02086-F1-model_v4',
 'AF-Q9HCS2-F1-model_

In [23]:
len(new_paths)

6252

In [26]:
# Obtener los elementos en lista1 pero no en lista2
diferencia1 = set(paths) - set(new_paths)

# Obtener los elementos en lista2 pero no en lista1
diferencia2 = set(new_paths) - set(paths)

# Imprimir los resultados
print("Elementos en new_paths pero no en paths:", diferencia1)
#print("Elementos en paths pero no en new_paths:", diferencia2)

Elementos en new_paths pero no en paths: {'AF-P28328-F1-model_v4', 'AF-B9A6J2-F1-model_v4', 'AF-Q7Z418-F1-model_v4', 'AF-Q6NUS6-F1-model_v4', 'AF-Q70EL2-F1-model_v4', 'AF-P98161-F15-model_v4', 'AF-Q8J025-F1-model_v4', 'AF-P23769-F1-model_v4', 'AF-O95180-F1-model_v4', 'AF-O15078-F1-model_v4', 'AF-A6NFK2-F1-model_v4', 'AF-Q14767-F1-model_v4', 'AF-P07384-F1-model_v4', 'AF-A0A0S2Z4W8-F1-model_v4', 'AF-Q5VIR6-F1-model_v4', 'AF-A0A0C4DFQ5-F1-model_v4', 'AF-Q14032-F1-model_v4', 'AF-Q6PGP7-F1-model_v4', 'AF-Q96CW9-F1-model_v4', 'AF-A8K881-F1-model_v4', 'AF-Q13510-F1-model_v4', 'AF-Q9NYF8-F1-model_v4', 'AF-O95528-F1-model_v4', 'AF-B2RDU6-F1-model_v4', 'AF-Q86X52-F1-model_v4', 'AF-P24821-F1-model_v4', 'AF-Q6IA86-F1-model_v4', 'AF-Q7L0Y3-F1-model_v4', 'AF-A0A140VKG2-F1-model_v4', 'AF-Q8N196-F1-model_v4', 'AF-A0A024R791-F1-model_v4', 'AF-P51160-F1-model_v4', 'AF-P50053-F1-model_v4', 'AF-Q9H1V8-F1-model_v4', 'AF-Q14790-F1-model_v4', 'AF-A0A0S2Z577-F1-model_v4', 'AF-P04920-F1-model_v4', 'AF-A0A076YI

In [28]:
folders_to_erase = list(diferencia1)

In [31]:
# Specify the path where the folders are located
gnomad_path = output_folder

# Specify the list of folder names to be deleted
folders_to_delete = folders_to_erase

# Get a list of all directories in the specified path
all_folders = next(os.walk(gnomad_path))[1]

# Iterate over the folders and delete the ones that match the names in the list
for folder_name in all_folders:
    if folder_name in folders_to_delete:
        folder_to_delete = os.path.join(gnomad_path, folder_name)
        # Use shutil.rmtree() to delete the entire folder and its contents
        shutil.rmtree(folder_to_delete)
        print(f"Deleted folder: {folder_to_delete}")

Deleted folder: /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/AF-P55157-F1-model_v4
Deleted folder: /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/AF-A6NFY7-F1-model_v4
Deleted folder: /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/AF-Q9Y448-F1-model_v4
Deleted folder: /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/AF-Q8N1V2-F1-model_v4
Deleted folder: /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/AF-A0A140VJR2-F1-model_v4
Deleted folder: /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/AF-A0A024R397-F1-model_v4
Deleted folder: /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/AF-P49902-F1-model_v4
Deleted folder: /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/AF-Q9UL51-F1-model_v4


### Make fasta files

In [ ]:
# Create the output folder if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

for path in gnomad_expanded['PDB_path'].unique():
    path = str(path)
    file_name = path.split("/")[-1].split(".")[0]
    # Create a PDB parser object
    parser = PDBParser()

    # Parse the PDB file
    structure = parser.get_structure(file_name, path)

    # Get the sequence from the first chain in the structure
    chains = structure.get_chains()
    
    prot_dict = {}
    for chain in chains:
        chain_id = chain.get_id()
        sequence = ''.join([protein_letters_3to1[residue.get_resname().lower().capitalize()] for residue in chain])
        print(sequence)
        prot_dict[chain_id] = sequence
        
    protein_folder = os.path.join(output_folder, file_name)
    os.makedirs(protein_folder, exist_ok=True)

    # Write the sequence to the FASTA file
    fasta_file = os.path.join(protein_folder, f'{file_name}.fasta')
    with open(fasta_file, 'w') as f:
        if len(prot_dict)==1:
            f.write(f'>{structure.id}\n')
            f.write(f'{sequence}\n')
        else:
            for key in prot_dict:
                f.write(f'>{structure.id}|{key}\n')
                f.write(f'{prot_dict[key]}\n')

MAGPAIHTAPMLFLVLLLPLELSLAGALAPGTPARNLPENHIDLPGPALWTPQASHHRRRGPGKKEWGPGLPSQAQDGAVVTATRQASRLPEAEGLLPEQSPAGLLQDKDLLLGLALPYPEKENRPPGWERTRKRSREHKRRRDRLRLHQGRALVRGPSSLMKKAELSEAQVLDAAMEESSTSLAPTMFFLTTFEAAPATEESLILPVTSLRPQQAQPRSDGEVMPTLDMALFDWTDYEDLKPDGWPSAKKKEKHRGKLSSDGNETSPAEGEPCDHHQDCLPGTCCDLREHLCTPHNRGLNNKCFDDCMCVEGLRCYAKFHRNRRVTRRKGRCVEPETANGDQGSFINV
MVNEARGNSSLNPCLEGSASSGSESSKDSSRCSTPGLDPERHERLREKMRRRLESGDKWFSLEFFPPRTAEGAVNLISRFDRMAAGGPLYIDVTWHPAGDPGSDKETSSMMIASTAVNYCGLETILHMTCCRQRLEEITGHLHKAKQLGLKNIMALRGDPIGDQWEEEEGGFNYAVDLVKHIRSEFGDYFDICVAGYPKGHPEAGSFEADLKHLKEKVSAGADFIITQLFFEADTFFRFVKACTDMGITCPIVPGIFPIQGYHSLRQLVKLSKLEVPQEIKDVIEPIKDNDAAIRNYGIELAVSLCQELLASGLVPGLHFYTLNREMATTEVLKRLGMWTEDPRRPLPWALSAHPKRREEDVRPIFWASRPKSYIYRTQEWDEFPNGRWGNSSSPAFGELKDYYLFYLKSKSPKEELLKMWGEELTSEESVFEVFVLYLSGEPNRNGHKVTCLPWNDEPLAAETSLLKEELLRVNRQGILTINSQPNINGKPSSDPIVGWGPSGGYVFQKAYLEFFTSRETAEALLQVLKKYELRVNYHLVNVKGENITNAPELQPNAVTWGIFPGREIIQPTVVDPVSFMFWKDEAFALWIERWGKLYEEESPSRTIIQYIHDNYFLVNLVDNDFPLDNCLWQVVEDTLELLNRPTQNA

In [20]:
subfolders = [f for f in os.listdir(output_folder) if os.path.isdir(os.path.join(output_folder, f))]

In [21]:
subfolders

['AF-Q9Y573-F1-model_v4',
 'AF-P82673-F1-model_v4',
 'AF-P59103-F1-model_v4',
 'AF-A0A024R2B6-F1-model_v4',
 'AF-A0A140VJG2-F1-model_v4',
 'AF-A0A024R2U1-F1-model_v4',
 'AF-Q9NQ79-F1-model_v4',
 'AF-O94955-F1-model_v4',
 'AF-A0A126GW71-F1-model_v4',
 'AF-Q6V1P9-F7-model_v4',
 'AF-A0FGR9-F1-model_v4',
 'AF-A0A384MEK2-F1-model_v4',
 'AF-Q01113-F1-model_v4',
 'AF-Q9NS39-F1-model_v4',
 'AF-Q9UJA9-F1-model_v4',
 'AF-A0A0S2Z634-F1-model_v4',
 'AF-Q5TEA3-F1-model_v4',
 'AF-Q92543-F1-model_v4',
 'AF-Q8N339-F1-model_v4',
 'AF-A0A024R922-F1-model_v4',
 'AF-O95727-F1-model_v4',
 'AF-P34096-F1-model_v4',
 'AF-Q9NU22-F13-model_v4',
 'AF-Q8N5U0-F1-model_v4',
 'AF-Q9BXA9-F1-model_v4',
 'AF-Q9Y3X0-F1-model_v4',
 'AF-A0A024RBT1-F1-model_v4',
 'AF-Q8TAT2-F1-model_v4',
 'AF-A0A024QZK8-F1-model_v4',
 'AF-P49418-F1-model_v4',
 'AF-Q86W67-F1-model_v4',
 'AF-A0A1B0GTG0-F1-model_v4',
 'AF-P06133-F1-model_v4',
 'AF-P22105-F15-model_v4',
 'AF-Q9NWY4-F1-model_v4',
 'AF-Q9HBK9-F1-model_v4',
 'AF-Q14183-F1-model_v

In [22]:
len(subfolders)

6254

In [23]:
paths_list = gnomad_expanded['PDB_path'].unique()

In [24]:
paths = [str(x).split("/")[-1].split(".")[0] for x in paths_list]

In [25]:
paths

['AF-Q8NBI3-F1-model_v4',
 'AF-P42898-F1-model_v4',
 'AF-P51797-F1-model_v4',
 'AF-P01160-F1-model_v4',
 'AF-Q02809-F1-model_v4',
 'AF-Q5JXC2-F1-model_v4',
 'AF-P20333-F1-model_v4',
 'AF-Q5THJ4-F5-model_v4',
 'AF-Q5VUY0-F1-model_v4',
 'AF-O95521-F1-model_v4',
 'AF-O60813-F1-model_v4',
 'AF-O60812-F1-model_v4',
 'AF-O60811-F1-model_v4',
 'AF-O60810-F1-model_v4',
 'AF-O60809-F1-model_v4',
 'AF-Q5VXH5-F1-model_v4',
 'AF-Q5VXH4-F1-model_v4',
 'AF-B2RXH8-F1-model_v4',
 'AF-A6NGN4-F1-model_v4',
 'AF-Q5TYX0-F1-model_v4',
 'AF-P0DUQ1-F1-model_v4',
 'AF-Q5SWL8-F1-model_v4',
 'AF-Q5VTA0-F1-model_v4',
 'AF-Q5VT99-F1-model_v4',
 'AF-Q86YL7-F1-model_v4',
 'AF-Q13029-F1-model_v4',
 'AF-Q674X7-F1-model_v4',
 'AF-P08218-F1-model_v4',
 'AF-P55211-F1-model_v4',
 'AF-A0A024QZ74-F1-model_v4',
 'AF-Q92681-F1-model_v4',
 'AF-Q8IWE5-F1-model_v4',
 'AF-A0PJX8-F1-model_v4',
 'AF-Q8WUP2-F1-model_v4',
 'AF-A0A096LP55-F1-model_v4',
 'AF-Q96T58-F2-model_v4',
 'AF-Q96T58-F3-model_v4',
 'AF-Q96T58-F9-model_v4',
 'AF

In [26]:
len(paths)

7698

In [27]:
# Obtener los elementos en lista1 pero no en lista2
diferencia1 = set(subfolders) - set(paths)

# Obtener los elementos en lista2 pero no en lista1
diferencia2 = set(paths) - set(subfolders)

# Imprimir los resultados
print("Elementos en subfolders pero no en paths:", diferencia1)
print("Elementos en paths pero no en subfolders:", diferencia2)

Elementos en subfolders pero no en paths: {'ibex_out', 'jobs'}
Elementos en paths pero no en subfolders: {'AF-P35212-F1-model_v4', 'AF-Q9NWX6-F1-model_v4', 'AF-Q5IJ48-F1-model_v4', 'AF-O00757-F1-model_v4', 'AF-Q96LB3-F1-model_v4', 'AF-P98161-F15-model_v4', 'AF-Q9ULD0-F1-model_v4', 'AF-A0A1B0GTW7-F1-model_v4', 'AF-P09936-F1-model_v4', 'AF-Q8NEN0-F1-model_v4', 'AF-P05141-F1-model_v4', 'AF-Q9BUK6-F1-model_v4', 'AF-Q96DT5-F16-model_v4', 'AF-Q9Y6Q6-F1-model_v4', 'AF-O95425-F1-model_v4', 'AF-Q99650-F1-model_v4', 'AF-Q96FX8-F1-model_v4', 'AF-A0A140VK45-F1-model_v4', 'AF-Q8IVH4-F1-model_v4', 'AF-Q9BVI0-F1-model_v4', 'AF-A0A140VKF7-F1-model_v4', 'AF-Q86SQ9-F1-model_v4', 'AF-P55157-F1-model_v4', 'AF-P13569-F1-model_v4', 'AF-Q9H161-F1-model_v4', 'AF-G0Z349-F1-model_v4', 'AF-O75072-F1-model_v4', 'AF-O94830-F1-model_v4', 'AF-B1ALW7-F1-model_v4', 'AF-P12111-F10-model_v4', 'AF-A1PUP8-F1-model_v4', 'AF-Q96M86-F1-model_v4', 'AF-Q8WYR4-F1-model_v4', 'AF-Q02218-F1-model_v4', 'AF-Q92508-F1-model_v4', 'AF-

### Make sbatch jobs for each protein

In [39]:
for protein_name in new_paths:
    protein_folder = os.path.join(output_folder, protein_name)
    fasta_path = os.path.join(protein_folder, f'{protein_name}.fasta')
    sbatch_file = os.path.join(output_folder, f'jobs/{protein_name}.sbatch')
    output_file = os.path.join(protein_folder, f'{protein_name}_PROP')
    
    with open(sbatch_file, 'w') as f:
        f.write("#!/bin/bash\n")
        f.write(f'#SBATCH -N 1\n')
        f.write(f"#SBATCH --job-name={protein_name}\n")
        f.write("#SBATCH --ntasks-per-node=1\n")
        f.write("#SBATCH --cpus-per-task=4\n")
        f.write("#SBATCH --mem=128\n")
        f.write("#SBATCH --time=12:00:00\n")
        f.write(f"#SBATCH --output=/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/ibex_out/{protein_name}.out\n")
        f.write(f"#SBATCH --error=/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/ibex_out/{protein_name}.err\n")
        f.write("#SBATCH --partition=batch\n")
        f.write(f"conda activate /ibex/scratch/penaguka/run_pipeline/variant_annotator/env\n")

        f.write("\n")
        f.write("# Run the RaptorX for each protein\n")
        f.write(f"/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/Predict_Property/Predict_Property.sh -i {fasta_path} -o {output_file}")

In [20]:
sorted_list = sorted(subfolders)

print(sorted_list)

['.ipynb_checkpoints', 'AF-A0A024QYX0-F1-model_v4', 'AF-A0A024QYX1-F1-model_v4', 'AF-A0A024QYX5-F1-model_v4', 'AF-A0A024QYX8-F1-model_v4', 'AF-A0A024QYY9-F1-model_v4', 'AF-A0A024QZ03-F1-model_v4', 'AF-A0A024QZ20-F1-model_v4', 'AF-A0A024QZ23-F1-model_v4', 'AF-A0A024QZ30-F1-model_v4', 'AF-A0A024QZ57-F1-model_v4', 'AF-A0A024QZ70-F1-model_v4', 'AF-A0A024QZ74-F1-model_v4', 'AF-A0A024QZ86-F1-model_v4', 'AF-A0A024QZA8-F1-model_v4', 'AF-A0A024QZA9-F1-model_v4', 'AF-A0A024QZB8-F1-model_v4', 'AF-A0A024QZD1-F1-model_v4', 'AF-A0A024QZE3-F1-model_v4', 'AF-A0A024QZE4-F1-model_v4', 'AF-A0A024QZF1-F1-model_v4', 'AF-A0A024QZP2-F1-model_v4', 'AF-A0A024QZQ2-F1-model_v4', 'AF-A0A024QZS1-F1-model_v4', 'AF-A0A024QZT2-F1-model_v4', 'AF-A0A024QZT7-F1-model_v4', 'AF-A0A024QZY1-F1-model_v4', 'AF-A0A024QZY7-F1-model_v4', 'AF-A0A024R040-F1-model_v4', 'AF-A0A024R050-F1-model_v4', 'AF-A0A024R064-F1-model_v4', 'AF-A0A024R068-F1-model_v4', 'AF-A0A024R089-F1-model_v4', 'AF-A0A024R0C3-F1-model_v4', 'AF-A0A024R0F8-F1-mo

In [138]:
for protein_name in rest:
    protein_folder = os.path.join(output_folder, protein_name)
    fasta_path = os.path.join(protein_folder, f'{protein_name}.fasta')
    sbatch_file = os.path.join(output_folder, f'jobs/{protein_name}.sbatch')
    output_file = os.path.join(protein_folder, f'{protein_name}_PROP')
    
    with open(sbatch_file, 'w') as f:
        f.write("#!/bin/bash\n")
        f.write(f'#SBATCH -N 1\n')
        f.write(f"#SBATCH --job-name={protein_name}\n")
        f.write("#SBATCH --ntasks-per-node=1\n")
        f.write("#SBATCH --cpus-per-task=4\n")
        f.write("#SBATCH --mem=128\n")
        f.write("#SBATCH --time=12:00:00\n")
        f.write(f"#SBATCH --output=/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ibex_out/{protein_name}.out\n")
        f.write(f"#SBATCH --error=/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ibex_out/{protein_name}.err\n")
        f.write("#SBATCH --partition=batch\n")
        f.write(f"conda activate /ibex/scratch/penaguka/run_pipeline/variant_annotator/env\n")

        f.write("\n")
        f.write("# Run the RaptorX for each protein\n")
        f.write(f"/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/Predict_Property/Predict_Property.sh -i {fasta_path} -o {output_file}")

### Run raptorX

In [46]:
smaller_newpaths = new_paths[0:1500]

In [42]:
for protein_name in smaller_newpaths:
    protein_folder = os.path.join(output_folder, protein_name)
    fasta_path = os.path.join(protein_folder, f'{protein_name}.fasta')
    command = f'sbatch /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/jobs/{protein_name}.sbatch'
    result = subprocess.run(command, shell=True, capture_output=True, text=True)

In [59]:
folder_path = '/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs'

In [ ]:
'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-P35556-F1-model_v4'

In [60]:
ss8_folders = []
for root, dirs, files in os.walk(output_folder):
    for file in files:
        file_name = file.split(".")[0]
        if file.endswith(".ss8"):
            ss8_folders.append(file_name)

In [29]:
ss8_folders

['AF-P82673-F1-model_v4',
 'AF-P59103-F1-model_v4',
 'AF-A0A024R2B6-F1-model_v4',
 'AF-A0A140VJG2-F1-model_v4',
 'AF-A0A024R2U1-F1-model_v4',
 'AF-O94955-F1-model_v4',
 'AF-Q6V1P9-F7-model_v4',
 'AF-A0FGR9-F1-model_v4',
 'AF-A0A384MEK2-F1-model_v4',
 'AF-Q01113-F1-model_v4',
 'AF-Q9NS39-F1-model_v4',
 'AF-Q9UJA9-F1-model_v4',
 'AF-A0A0S2Z634-F1-model_v4',
 'AF-Q5TEA3-F1-model_v4',
 'AF-Q92543-F1-model_v4',
 'AF-Q8N339-F1-model_v4',
 'AF-A0A024R922-F1-model_v4',
 'AF-O95727-F1-model_v4',
 'AF-P34096-F1-model_v4',
 'AF-Q9NU22-F13-model_v4',
 'AF-Q8N5U0-F1-model_v4',
 'AF-Q9Y3X0-F1-model_v4',
 'AF-A0A024RBT1-F1-model_v4',
 'AF-Q86W67-F1-model_v4',
 'AF-A0A1B0GTG0-F1-model_v4',
 'AF-P06133-F1-model_v4',
 'AF-P22105-F15-model_v4',
 'AF-Q9NWY4-F1-model_v4',
 'AF-Q9HBK9-F1-model_v4',
 'AF-Q14183-F1-model_v4',
 'AF-P0DMQ9-F1-model_v4',
 'AF-Q15485-F1-model_v4',
 'AF-Q9BQ51-F1-model_v4',
 'AF-A0A0A0MR39-F1-model_v4',
 'AF-Q8N398-F1-model_v4',
 'AF-Q9Y3R4-F1-model_v4',
 'AF-Q4G0U5-F1-model_v4',


In [61]:
len(ss8_folders)

5999

In [62]:
# Obtener los elementos en lista1 pero no en lista2
diferencia1 = set(ss8_folders) - set(new_paths)

# Obtener los elementos en lista2 pero no en lista1
diferencia2 = set(new_paths) - set(ss8_folders)

# Imprimir los resultados
#print("Elementos en ss8_folders pero no en paths:", diferencia1)
#print("Elementos en paths pero no en ss8_folders:", diferencia2)

In [63]:
rest = list(diferencia2)

In [55]:
rest

['AF-Q15751-F9-model_v4',
 'AF-Q96MA6-F1-model_v4',
 'AF-Q8NCG7-F1-model_v4',
 'AF-A0A024RBS0-F1-model_v4',
 'AF-Q9BS31-F1-model_v4',
 'AF-P0DJR0-F1-model_v4',
 'AF-A6NDS4-F1-model_v4',
 'AF-A0A024RCH3-F1-model_v4',
 'AF-Q8N8V2-F1-model_v4',
 'AF-Q12788-F1-model_v4',
 'AF-Q5JR59-F1-model_v4',
 'AF-Q9BRX2-F1-model_v4',
 'AF-A6NHA9-F1-model_v4',
 'AF-A5D8W1-F1-model_v4',
 'AF-Q6P9B6-F1-model_v4',
 'AF-Q8NBM8-F1-model_v4',
 'AF-Q9GZK7-F1-model_v4',
 'AF-Q6L8H2-F1-model_v4',
 'AF-A0A140VJN2-F1-model_v4',
 'AF-P13611-F5-model_v4',
 'AF-Q15751-F6-model_v4',
 'AF-Q5VT66-F1-model_v4',
 'AF-Q8N999-F1-model_v4',
 'AF-Q5VWC8-F1-model_v4',
 'AF-A0A2R8Y5H9-F1-model_v4',
 'AF-Q5T4I8-F1-model_v4',
 'AF-C9JL84-F1-model_v4',
 'AF-Q8N9V7-F1-model_v4',
 'AF-Q504Y0-F1-model_v4',
 'AF-Q9HC84-F7-model_v4',
 'AF-P0DPF3-F1-model_v4',
 'AF-O43290-F1-model_v4',
 'AF-Q8NH51-F1-model_v4',
 'AF-Q8TDY8-F1-model_v4',
 'AF-Q6NUJ5-F1-model_v4',
 'AF-Q8N1F8-F1-model_v4',
 'AF-Q86T75-F1-model_v4',
 'AF-O14633-F1-model_v

In [64]:
len(rest)

253

In [57]:
less_rest = rest[0:1500]

In [65]:
less_rest = rest

In [85]:
less_rest

['AF-A0A024QZ70-F1-model_v4',
 'AF-Q14315-F5-model_v4',
 'AF-Q02505-F1-model_v4',
 'AF-A1PUP8-F1-model_v4',
 'AF-Q12791-F1-model_v4',
 'AF-J3KNI1-F1-model_v4',
 'AF-A0A3B3ISR2-F1-model_v4',
 'AF-Q8NET8-F1-model_v4',
 'AF-Q7Z3E5-F1-model_v4',
 'AF-P08069-F1-model_v4',
 'AF-O75112-F1-model_v4',
 'AF-Q99996-F6-model_v4',
 'AF-Q13009-F1-model_v4',
 'AF-Q9HC78-F1-model_v4',
 'AF-P98161-F3-model_v4',
 'AF-O95267-F1-model_v4',
 'AF-P40692-F1-model_v4',
 'AF-Q8NCM8-F8-model_v4',
 'AF-Q15751-F19-model_v4',
 'AF-Q14980-F1-model_v4',
 'AF-P16885-F1-model_v4',
 'AF-Q9HCE0-F1-model_v4',
 'AF-Q9UKP5-F1-model_v4',
 'AF-Q99698-F2-model_v4',
 'AF-P00747-F1-model_v4',
 'AF-Q93063-F1-model_v4',
 'AF-P27708-F1-model_v4',
 'AF-Q8IWN7-F1-model_v4',
 'AF-P49736-F1-model_v4',
 'AF-Q9UKY4-F1-model_v4',
 'AF-P78504-F1-model_v4',
 'AF-O75445-F19-model_v4',
 'AF-P78509-F10-model_v4',
 'AF-P42858-F10-model_v4',
 'AF-Q8WXX7-F1-model_v4',
 'AF-Q9ULW8-F1-model_v4',
 'AF-Q9BYN7-F1-model_v4',
 'AF-P47989-F1-model_v4',


In [58]:
import subprocess

In [66]:
for protein_name in less_rest:
    protein_folder = os.path.join(output_folder, protein_name)
    fasta_path = os.path.join(protein_folder, f'{protein_name}.fasta')
    command = f'sbatch /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/jobs/{protein_name}.sbatch'
    result = subprocess.run(command, shell=True, capture_output=True, text=True)

In [51]:
!squeue -u penaguka

             JOBID PARTITION     NAME     USER ST       TIME  NODES NODELIST(REASON)
          26078840     batch  jupyter penaguka  R    1:28:24      1 cn605-23-r


In [ ]:
['AF-A0A0S2Z4G5-F1-model_v4.seq', 'AF-A0A0S2Z4G5-F1-model_v4.summary', 'AF-A0A0S2Z4G5-F1-model_v4.tm8', 'AF-A0A0S2Z4G5-F1-model_v4.ss3_simp', 'AF-A0A0S2Z4G5-F1-model_v4.ss8_simp', 'AF-A0A0S2Z4G5-F1-model_v4.diso', 'AF-A0A0S2Z4G5-F1-model_v4.all', 'AF-A0A0S2Z4G5-F1-model_v4.fasta', 'AF-A0A0S2Z4G5-F1-model_v4.tm8_simp', 'AF-A0A0S2Z4G5-F1-model_v4.tm2', '0README_noprof', '.ss8', '.acc', '.acc_simp', '.ss3', '.diso_simp', '.tm2_simp']

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-A0A0S2Z4G5-F1-model_v4/AF-A0A0S2Z4G5-F1-model_v4.all

In [ ]:
sbatch AF-Q63HN8-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q9BYI3-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q7Z6Z7-F10-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q9NZW4-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/jobs/AF-Q14204-F11-model_v4.sbatch

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q5VTB9-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q8WZ42-F13-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q9Y2H9-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q8WZ42-F1-model_v4

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q8WZ42-F3-model_v4

In [ ]:
AF-Q8WZ42-F2-model_v4]$ cd /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ibex_out/AF-Q8WZ42-F3-model_v4.err

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q14204-F11-model_v4

In [ ]:
 AF-A0A0S2Z4G5-F1-model_v4_PROP

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-A0A0S2Z4G5-F1-model_v4

In [ ]:
cd /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-P35556-F1-model_v4

In [ ]:
find /ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/ -type d -name 'TMP_TGTGEN_*' -exec rm -r {} \;

In [ ]:
/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-A0A0S2Z4G5-F1-model_v4/AF-A0A0S2Z4G5-F1-model_v4_PROP/AF-A0A0S2Z4G5-F1-model_v4.all

### Add raptor x notations

In [9]:
gnomad_full = gnomad_expanded.copy()

In [10]:
gnomad_full.isnull().sum()

#CHROM                        0
POS                           0
ID                            0
REF                           0
ALT                           0
AC                            0
AF                            0
AN                            0
QD                            0
variant_type                  0
vep                           0
flags                         0
Allele                        0
Consequence                   0
IMPACT                        0
SYMBOL                        3
Gene                          0
Feature_type                  0
Feature                       0
BIOTYPE                       0
EXON                          0
INTRON                    15941
HGVSc                     15941
HGVSp                     15941
cDNA_position                 0
CDS_position                  0
Protein_position              0
Amino_acids                   0
Codons                        0
Existing_variation           10
DISTANCE                  15941
STRAND  

In [11]:
gnomad_full

#CHROM       POS            ID REF ALT      AC         AF      AN  \
0       chr1  11706367    rs11121804   C   T   39444   0.158732  248494   
1       chr1  11790870     rs2274976   C   T   13949  0.0555184  251250   
2       chr1  11824498      rs198400   A   G  250947   0.999399  251098   
3       chr1  11847591        rs5063   C   T   14048  0.0558586  251492   
4       chr1  11949899     rs7551175   G   A   45490   0.180978  251356   
5       chr1  11950412     rs2273285   G   T   21778  0.0866876  251224   
6       chr1  12022277    rs11553925   A   T   49896   0.199681  249878   
7       chr1  12022404    rs11588712   C   T   27588   0.119221  231402   
8       chr1  12022869     rs2295283   A   G  165360   0.682133  242416   
9       chr1  12192898     rs1061622   T   G   54148   0.216294  250344   
10      chr1  12279562     rs4845898   A   T   55150   0.219676  251052   
11      chr1  12725782    rs11121969   C   T   14579  0.0584929  249244   
12      chr1  12794279     rs1769774   C   T   77773   0.310838  250204   
13      chr1  12795729     rs1052908   A   C   50855   0.268197  189618   
14      chr1  12828511   rs200394590   T   G   28573   0.212483  134472   
15      chr1  12847526    rs74055698   T   C   40607   0.176483  230090   
16      chr1  12847643   rs138700801   T   C   12357  0.0503603  245372   
17      chr1  12847680   rs141872266   T   C   13186   0.053552  246228   
18      chr1  12859108     rs9661554   G   T   26002    0.10414  249682   
19      chr1  12859209     rs3204790   T   G   40973    0.16561  247406   
20      chr1  12859224     rs9659529   C   G   26417   0.105534  250318   
21      chr1  12859226    rs45443899   C   T   26237   0.104801  250350   
22      chr1  12859769    rs80027487   C   G   25356   0.101816  249038   
23      chr1  12860017     rs3204798   T   G   14546  0.0586551  247992   
24      chr1  12860073    rs72472698   A   G   26776   0.107356  249414   
...      ...       ...           ...  ..  ..     ...        ...     ...   
15916   chrX  50376086     rs4074320   C   T   41414   0.231714  178729   
15917   chrX  50911091    rs41308602   A   G    7747  0.0570719  135741   
15918   chrX  52645464   rs112382781   G   T   16845  0.0979064  172052   
15919   chrX  54755097    rs17316491   C   G   11594  0.0642555  180436   
15920   chrX  54925031    rs45448595   C   T   10765  0.0596419  180494   
15921   chrX  55090033     rs1845444   C   G  177865   0.979125  181657   
15922   chrX  55263341     rs4826381   T   C  169359   0.933792  181367   
15923   chrX  55624568     rs2375465   T   C  170097   0.934383  182042   
15924   chrX  57136462     rs2003812   G   A   41123    0.93108   44167   
15925   chrX  57592412   rs199513692   G   A    4161   0.050147   82976   
15926   chrX  57592416   rs200267267   A   C    4385  0.0567322   77293   
15927   chrX  57592437   rs189164178   G   A   10971   0.168288   65192   
15928   chrX  66602765     rs1385698   T   C  149078   0.980931  151976   
15929   chrX  66605144     rs1385699   C   T  140733   0.793474  177363   
15930   chrX  68432906    rs41303733   C   T   10488  0.0572795  183102   
15931   chrX  69505797     rs1171942   T   C   89348   0.492984  181239   
15932   chrX  70258925     rs3829709   A   C   20562   0.114082  180239   
15933   chrX  70259092     rs1152187   T   G   42510   0.232866  182551   
15934   chrX  70341930     rs1199457   T   G   10828  0.0613596  176468   
15935   chrX  70926625     rs6525447   G   C   36218   0.238416  151911   
15936   chrX  72140250     rs7061150   C   T   12196  0.0674621  180783   
15937   chrY   6246522   rs201475959   A   G    1025  0.0780952   13125   
15938   chrY  12720687     rs7067496   G   T    6033  0.0894759   67426   
15939   chrY  22180292  rs1478920645   G   T       1   0.142857       7   
15940   chrY  22406127  rs1195699969   C   A       9          1       9   

          QD variant_type                                                vep  \
0      13.47        mixed

In [12]:
column_names = ['ss8_pred', 'ss8_H', 'ss8_G', 'ss8_I', 'ss8_E', 'ss8_B', 'ss8_T', 'ss8_S', 'ss8_L',
                'acc_pred', 'acc_B', 'acc_M', 'acc_E',
                'diso_pred', 'diso_score',
                'tm8_pred', 'tm8_H', 'tm8_E', 'tm8_C', 'tm8_I', 'tm8_L', 'tm8_F', 'tm8_X', 'tm8__']

# Add new columns to the dataframe with no values
gnomad_full[column_names] = pd.DataFrame(columns=column_names)

In [13]:
maxasa_dict = {
    'A': 113,
    'R': 241,
    'N': 158,
    'D': 151,
    'C': 140,
    'E': 183,
    'Q': 189,
    'G': 85,
    'H': 194,
    'I': 182,
    'L': 180,
    'K': 211,
    'M': 204,
    'F': 218,
    'P': 143,
    'S': 122,
    'T': 146,
    'W': 259,
    'Y': 229,
    'V': 160
}

In [14]:
def assign_access_letter(access):
    if access <= 50:
        return 'B'
    elif access <= 100:
        return 'M'
    else:
        return 'E'

In [15]:
def assign_acc(access):
    if access <= 12:
        return 'B'
    elif access <= 42:
        return 'M'
    else:
        return 'E'

In [16]:
def retrieve_data(df,index,pos,aa):
    if (temp_df['position'].iloc[pos-1] == pos) & (temp_df['AA'].iloc[pos-1] == aa):
        for column in column_names:
            df.at[index, column] = temp_df[column].iloc[pos-1]

In [17]:
def get_raptorx(file_path):
    
    # Read the file
    with open(file_path, 'r') as file:
        file_content = file.read()
        
    # Extract SS8 predictions
    ss8_start = file_content.find('#---------------- details of SS8 prediction ---------------------------')
    ss8_end = file_content.find('#---------------- details of ACC prediction ---------------------------')
    ss8_lines = file_content[ss8_start: ss8_end]  
    #print(ss8_lines)
    # Extract ACC predictions
    acc_start = file_content.find('#---------------- details of ACC prediction ---------------------------')
    acc_end = file_content.find('#---------------- details of DISO prediction --------------------------')
    acc_lines = file_content[acc_start: acc_end]
    # Extract DISO predictions
    diso_start = file_content.find('#---------------- details of DISO prediction --------------------------')
    diso_end = file_content.find('#---------------- details of TM2 prediction ---------------------------')
    diso_lines = file_content[diso_start: diso_end]
    # Extract TM8 predictions
    tm8_start = file_content.find('#---------------- details of TM8 prediction ---------------------------')
    tm8_end = len(file_content)
    tm8_lines = file_content[tm8_start:tm8_end]
        
    # Create a ss8 DataFrame from the lines
    ss8_columns = ['position', 'AA','ss8_pred','ss8_H','ss8_G','ss8_I','ss8_E','ss8_B','ss8_T','ss8_S','ss8_L']
    ss8_rows = [line.strip() for line in ss8_lines.split('\n') if not line.startswith('#')]
    ss8_values = [row.split() for row in ss8_rows]
    data_ss8 = pd.DataFrame(ss8_values, columns=ss8_columns)
    data_ss8.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = ss8_columns[3:]
    pos_column = ss8_columns[0]
    data_ss8[numeric_columns] = data_ss8[numeric_columns].astype(float)
    data_ss8[pos_column] = data_ss8[pos_column].astype(int)
    
    # Create an acc DataFrame from the lines
    acc_columns = ['position', 'AA','acc_pred','acc_B','acc_M','acc_E']
    acc_rows = [line.strip() for line in acc_lines.split('\n') if not line.startswith('#')]
    acc_values = [row.split() for row in acc_rows]
    data_acc = pd.DataFrame(acc_values, columns=acc_columns)
    data_acc.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = acc_columns[3:]
    pos_column = acc_columns[0]
    data_acc[numeric_columns] = data_acc[numeric_columns].astype(float)
    data_acc[pos_column] = data_acc[pos_column].astype(int)
    
    # Create an diso DataFrame from the lines
    diso_columns = ['position', 'AA','diso_pred','diso_score']
    diso_rows = [line.strip() for line in diso_lines.split('\n') if not line.startswith('#')]
    diso_values = [row.split() for row in diso_rows]
    data_diso = pd.DataFrame(diso_values, columns=diso_columns)
    data_diso.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = diso_columns[3:]
    pos_column = diso_columns[0]
    data_diso[numeric_columns] = data_diso[numeric_columns].astype(float)
    data_diso[pos_column] = data_diso[pos_column].astype(int)
    
    # Create an acc DataFrame from the lines
    tm8_columns = ['position', 'AA','tm8_pred','tm8_H','tm8_E','tm8_C','tm8_I','tm8_L','tm8_F','tm8_X','tm8__']
    tm8_rows = [line.strip() for line in tm8_lines.split('\n') if not line.startswith('#')]
    tm8_values = [row.split() for row in tm8_rows]
    data_tm8 = pd.DataFrame(tm8_values, columns=tm8_columns)
    data_tm8.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = tm8_columns[3:]
    pos_column = tm8_columns[0]
    data_tm8[numeric_columns] = data_tm8[numeric_columns].astype(float)
    data_tm8[pos_column] = data_tm8[pos_column].astype(int)

    # Optionally, you can set column names
    big_df = pd.DataFrame()
    if all(df['position'].equals(data_ss8['position']) and df['AA'].equals(data_ss8['AA']) for df in [data_acc, data_diso, data_tm8]):
        # If the columns are equal, keep only one copy at the beginning of big_df
        big_df = pd.concat([data_ss8, data_acc.iloc[:, 2:], data_diso.iloc[:, 2:], data_tm8.iloc[:, 2:]], axis=1)
    else:
        # If the columns are not equal, concatenate all dataframes as usual
        print(f'Positions and AAs do not match between data_ss8, data_acc, data_diso, data_tm8 of {file_path}.')
        big_df = pd.concat([data_ss8, data_acc, data_diso, data_tm8], axis=1)
        
    #column_names = ['position', 'AA','ss_H','ss_G','ss_I','ss_E','ss_B','ss_T','ss_S','ss_L','acc_B','acc_M','acc_E','diso_score','tm8_H','tm8_E','tm8_C','tm8_I','tm8_L','tm8_F','tm8_X','tm8__']  # Replace with your actual column names
    #big_df.columns = column_names

    # Create a DataFrame from the extracted data
    return big_df

In [32]:
for item in gnomad_full['PDB_path'].unique():
    path = item
    protein = str(path).split("/")[-1].split(".")[0]
    if protein in already_done:
        raptorx_preds = f'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/{protein}/{protein}_PROP/{protein}.all'
    elif protein in new_paths:
        raptorx_preds = f'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/{protein}/{protein}_PROP/{protein}.all'
    else:
        print(f'No RaptorX output for {protein}')
    temp_df = get_raptorx(raptorx_preds)
    for index, row in gnomad_full[gnomad_full['PDB_path'] == path].iterrows():
        #print(index)
        # Access the row data using row['column_name'] or row[column_index]
        # modify the row values directly
        # For example, update a specific column value
        pos = gnomad_full['Residue_position'].iloc[index]
        aa = protein_letters_3to1[gnomad_full['WT'].iloc[index]]
        match = re.search(r'-F(-?\d+)-', protein)
        if match:
            number = int(match.group(1))
            if number == 1:
                retrieve_data(gnomad_full,index,pos,aa)
            else:
                temp_pos = pos-((number-1)*200)
                retrieve_data(gnomad_full,index,temp_pos,aa)
        else:
            print(f"No number found for {protein}.")

In [33]:
gnomad_full

#CHROM       POS            ID REF ALT      AC         AF      AN  \
0       chr1  11706367    rs11121804   C   T   39444   0.158732  248494   
1       chr1  11790870     rs2274976   C   T   13949  0.0555184  251250   
2       chr1  11824498      rs198400   A   G  250947   0.999399  251098   
3       chr1  11847591        rs5063   C   T   14048  0.0558586  251492   
4       chr1  11949899     rs7551175   G   A   45490   0.180978  251356   
5       chr1  11950412     rs2273285   G   T   21778  0.0866876  251224   
6       chr1  12022277    rs11553925   A   T   49896   0.199681  249878   
7       chr1  12022404    rs11588712   C   T   27588   0.119221  231402   
8       chr1  12022869     rs2295283   A   G  165360   0.682133  242416   
9       chr1  12192898     rs1061622   T   G   54148   0.216294  250344   
10      chr1  12279562     rs4845898   A   T   55150   0.219676  251052   
11      chr1  12725782    rs11121969   C   T   14579  0.0584929  249244   
12      chr1  12794279     rs1769774   C   T   77773   0.310838  250204   
13      chr1  12795729     rs1052908   A   C   50855   0.268197  189618   
14      chr1  12828511   rs200394590   T   G   28573   0.212483  134472   
15      chr1  12847526    rs74055698   T   C   40607   0.176483  230090   
16      chr1  12847643   rs138700801   T   C   12357  0.0503603  245372   
17      chr1  12847680   rs141872266   T   C   13186   0.053552  246228   
18      chr1  12859108     rs9661554   G   T   26002    0.10414  249682   
19      chr1  12859209     rs3204790   T   G   40973    0.16561  247406   
20      chr1  12859224     rs9659529   C   G   26417   0.105534  250318   
21      chr1  12859226    rs45443899   C   T   26237   0.104801  250350   
22      chr1  12859769    rs80027487   C   G   25356   0.101816  249038   
23      chr1  12860017     rs3204798   T   G   14546  0.0586551  247992   
24      chr1  12860073    rs72472698   A   G   26776   0.107356  249414   
...      ...       ...           ...  ..  ..     ...        ...     ...   
15916   chrX  50376086     rs4074320   C   T   41414   0.231714  178729   
15917   chrX  50911091    rs41308602   A   G    7747  0.0570719  135741   
15918   chrX  52645464   rs112382781   G   T   16845  0.0979064  172052   
15919   chrX  54755097    rs17316491   C   G   11594  0.0642555  180436   
15920   chrX  54925031    rs45448595   C   T   10765  0.0596419  180494   
15921   chrX  55090033     rs1845444   C   G  177865   0.979125  181657   
15922   chrX  55263341     rs4826381   T   C  169359   0.933792  181367   
15923   chrX  55624568     rs2375465   T   C  170097   0.934383  182042   
15924   chrX  57136462     rs2003812   G   A   41123    0.93108   44167   
15925   chrX  57592412   rs199513692   G   A    4161   0.050147   82976   
15926   chrX  57592416   rs200267267   A   C    4385  0.0567322   77293   
15927   chrX  57592437   rs189164178   G   A   10971   0.168288   65192   
15928   chrX  66602765     rs1385698   T   C  149078   0.980931  151976   
15929   chrX  66605144     rs1385699   C   T  140733   0.793474  177363   
15930   chrX  68432906    rs41303733   C   T   10488  0.0572795  183102   
15931   chrX  69505797     rs1171942   T   C   89348   0.492984  181239   
15932   chrX  70258925     rs3829709   A   C   20562   0.114082  180239   
15933   chrX  70259092     rs1152187   T   G   42510   0.232866  182551   
15934   chrX  70341930     rs1199457   T   G   10828  0.0613596  176468   
15935   chrX  70926625     rs6525447   G   C   36218   0.238416  151911   
15936   chrX  72140250     rs7061150   C   T   12196  0.0674621  180783   
15937   chrY   6246522   rs201475959   A   G    1025  0.0780952   13125   
15938   chrY  12720687     rs7067496   G   T    6033  0.0894759   67426   
15939   chrY  22180292  rs1478920645   G   T       1   0.142857       7   
15940   chrY  22406127  rs1195699969   C   A       9          1       9   

          QD variant_type                                                vep  \
0      13.47        mixed

In [34]:
gnomad_full.isnull().sum()

#CHROM                        0
POS                           0
ID                            0
REF                           0
ALT                           0
AC                            0
AF                            0
AN                            0
QD                            0
variant_type                  0
vep                           0
flags                         0
Allele                        0
Consequence                   0
IMPACT                        0
SYMBOL                        3
Gene                          0
Feature_type                  0
Feature                       0
BIOTYPE                       0
EXON                          0
INTRON                    15941
HGVSc                     15941
HGVSp                     15941
cDNA_position                 0
CDS_position                  0
Protein_position              0
Amino_acids                   0
Codons                        0
Existing_variation           10
DISTANCE                  15941
STRAND  

In [36]:
gnomad_full['tm8_pred'].value_counts()

_    11420
X     2925
H     1174
E      422
Name: tm8_pred, dtype: int64

In [37]:
gnomad_full['acc_DSSP'] = gnomad_full['accessibility'].apply(assign_access_letter)

In [40]:
gnomad_full['WT'] = gnomad_full['WT'].map(protein_letters_3to1)

In [41]:
gnomad_full['MUT'] = gnomad_full['MUT'].map(protein_letters_3to1)

In [43]:
gnomad_full['RSA'] = (gnomad_full['accessibility'] / (gnomad_full['WT'].map(maxasa_dict)))*100

In [44]:
gnomad_full['acc_RSA'] = gnomad_full['RSA'].apply(assign_acc)

In [45]:
gnomad_full['acc_match'] = np.where((gnomad_full['acc_DSSP'] == gnomad_full['acc_pred'])
                                        & (~gnomad_full['acc_DSSP'].isnull())
                                        & (~gnomad_full['acc_pred'].isnull()), 1,
                                        np.where(gnomad_full['acc_DSSP'].isnull()
                                                 | gnomad_full['acc_pred'].isnull(), np.nan, 0))

In [47]:
gnomad_full['acc_match_RSA'] = np.where((gnomad_full['acc_RSA'] == gnomad_full['acc_pred'])
                                        & (~gnomad_full['acc_RSA'].isnull())
                                        & (~gnomad_full['acc_pred'].isnull()), 1,
                                        np.where(gnomad_full['acc_RSA'].isnull()
                                                 | gnomad_full['acc_pred'].isnull(), np.nan, 0))

In [52]:
gnomad_full[['acc_DSSP','acc_pred','acc_match','acc_RSA','acc_match_RSA','acc_B','acc_M','acc_E','accessibility']]

acc_DSSP acc_pred  acc_match acc_RSA  acc_match_RSA  acc_B  acc_M  \
0            E        B        0.0       E            0.0  0.455  0.437   
1            B        M        0.0       B            0.0  0.144  0.596   
2            B        E        0.0       B            0.0   0.17  0.385   
3            M        B        0.0       E            0.0  0.495  0.325   
4            B        B        1.0       B            1.0  0.878  0.105   
5            B        B        1.0       M            0.0  0.493  0.341   
6            E        E        1.0       E            1.0  0.045  0.189   
7            E        E        1.0       E            1.0  0.356  0.255   
8            E        E        1.0       E            1.0  0.085  0.299   
9            E        B        0.0       E            0.0  0.506  0.335   
10           E        E        1.0       E            1.0  0.076  0.352   
11           B        E        0.0       M            0.0  0.186  0.397   
12           B        E        0.0       M            0.0  0.075  0.298   
13           E        E        1.0       E            1.0  0.132  0.427   
14           M        E        0.0       E            1.0  0.016  0.207   
15           E        E        1.0       E            1.0  0.046  0.008   
16           E        E        1.0       E            1.0  0.015  0.019   
17           M        E        0.0       E            1.0  0.117  0.183   
18           E        M        0.0       E            0.0  0.185  0.537   
19           B        B        1.0       B            1.0  0.609  0.319   
20           M        E        0.0       E            1.0  0.152   0.41   
21           B        M        0.0       M            1.0  0.414  0.464   
22           E        B        0.0       E            0.0  0.587  0.308   
23           B        B        1.0       M            0.0  0.857  0.104   
24           B        M        0.0       M            1.0  0.118  0.548   
...        ...      ...        ...     ...            ...    ...    ...   
15916        E        M        0.0       E            0.0  0.325  0.405   
15917        B        E        0.0       M            0.0  0.208  0.337   
15918        E        E        1.0       E            1.0  0.015  0.081   
15919        E        B        0.0       E            0.0  0.457    0.4   
15920        M        E        0.0       M            0.0  0.051  0.369   
15921        E        E        1.0       E            1.0  0.349  0.063   
15922        M        E        0.0       E            1.0  0.064  0.096   
15923        M        E        0.0       E            1.0  0.172  0.269   
15924        E        E        1.0       E            1.0  0.072  0.239   
15925        E        E        1.0       E            1.0  0.018   0.04   
15926        E        E        1.0       E            1.0  0.035  0.039   
15927        M        E        0.0       E            1.0  0.188  0.029   
15928        M        E        0.0       E            1.0  0.103  0.378   
15929        E        M        0.0       E            0.0  0.174  0.454   
15930        B        B        1.0       M            0.0  0.547  0.308   
15931        E        E        1.0       E            1.0  0.227  0.081   
15932        B        E        0.0       M            0.0  0.059  0.142   
15933        E        E        1.0       E            1.0  0.066  0.282   
15934        M        E        0.0       E            1.0  0.081   0.34   
15935        E        E        1.0       E            1.0  0.136  0.354   
15936        E        E        1.0       E            1.0  0.173  0.147   
15937        E        E        1.0       E            1.0  0.015  0.252   
15938        M        E        0.0       E            1.0  0.054  0.061   
15939        B        E        0.0       M            0.0  0.228  0.371   
15940        B        E        0.0       M            0.0  0.228  0.371   

       acc_E  accessibility  
0      0.107            144  
1       0.26             27  
2      0.444   

In [50]:
gnomad_full['acc_match'].value_counts()

1.0    8201
0.0    7740
Name: acc_match, dtype: int64

In [51]:
gnomad_full['acc_match_RSA'].value_counts()

1.0    9461
0.0    6480
Name: acc_match_RSA, dtype: int64

In [8]:
gnomad_full['ss_match'] = np.where((gnomad_full['secondary_structure'] == gnomad_full['ss8_pred'])
                                        & (~gnomad_full['secondary_structure'].isnull())
                                        & (~gnomad_full['ss8_pred'].isnull()), 1,
                                        np.where(gnomad_full['secondary_structure'].isnull()
                                                 | gnomad_full['ss8_pred'].isnull(), np.nan, 0))

In [9]:
gnomad_full['ss_match'] = gnomad_full['ss_match'].astype('Int64')

In [10]:
gnomad_full['ss_match'].isnull().sum()

0

In [11]:
gnomad_full['ss_match'].value_counts()

1    10333
0     5608
Name: ss_match, dtype: Int64

In [12]:
gnomad_full[['secondary_structure','ss8_pred','ss_match', 'prot_length']]

secondary_structure ss8_pred  ss_match  prot_length
0                       L        L         1          349
1                       I        H         0          656
2                       B        H         0          869
3                       L        L         1          151
4                       E        E         1          727
...                   ...      ...       ...          ...
15936                   L        L         1         1225
15937                   H        H         1          308
15938                   L        L         1         2555
15939                   L        L         1          496
15940                   L        L         1          496

[15941 rows x 4 columns]

In [13]:
gnomad_full.to_pickle('gnomad_full.pkl')

In [5]:
gnomad_full = pd.read_pickle('gnomad_full.pkl')

In [6]:
gnomad_full['secondary_structure'] = gnomad_full['secondary_structure'].fillna('L')

In [7]:
gnomad_full['secondary_structure'].value_counts()

L    7347
H    4503
E    1543
T    1179
S     893
G     328
B      83
I      65
Name: secondary_structure, dtype: int64

In [82]:
top_rows = gnomad_full.nlargest(1000, 'prot_length')

In [77]:
top_rows[['secondary_structure','ss8_pred','ss_match', 'prot_length']]

secondary_structure ss8_pred  ss_match  prot_length
5793                    H        H         1         8797
5794                  NaN        L      <NA>         8797
5795                  NaN        L      <NA>         8797
5796                  NaN        L      <NA>         8797
5797                    H        H         1         8797
5798                    H        H         1         8797
5799                    H        H         1         8797
5800                    H        H         1         8797
5801                    H        H         1         8797
5802                    H        H         1         8797
5803                    S        L         0         8797
5804                    H        H         1         8797
5805                    H        H         1         8797
5806                    H        H         1         8797
2536                  NaN        L      <NA>         8525
2537                  NaN        L      <NA>         8525
2538                  NaN        E      <NA>         8525
2539                  NaN        E      <NA>         8525
2540                    H        H         1         8525
2541                    H        H         1         8525
2542                    H        H         1         8525
2543                    H        H         1         8525
2544                    H        H         1         8525
2545                    H        H         1         8525
2546                  NaN        E      <NA>         8525
2547                  NaN        E      <NA>         8525
2548                    H        H         1         8525
2549                    H        H         1         8525
2550                    T        H         0         8525
2551                    T        H         0         8525
1805                  NaN        E      <NA>         6907
1806                    H        H         1         6907
1807                    T        T         1         6907
1808                    H        H         1         6907
1809                    S        H         0         6907
1810                  NaN        L      <NA>         6907
1811                  NaN        T      <NA>         6907
1812                  NaN        E      <NA>         6907
1813                  NaN        L      <NA>         6907
1814                    H        H         1         6907
1815                  NaN        L      <NA>         6907
1816                  NaN        H      <NA>         6907
1817                  NaN        T      <NA>         6907
1818                  NaN        L      <NA>         6907
1819                  NaN        H      <NA>         6907
1820                    H        H         1         6907
1821                    H        H         1         6907
1822                    H        H         1         6907
1823                    H        H         1         6907
1824                  NaN        H      <NA>         6907
1825                  NaN        E      <NA>         6907
1826                  NaN        L      <NA>         6907
1827                    T        T         1         6907
1828                  NaN        L      <NA>         6907
1829                  NaN        H      <NA>         6907
1830                    H        H         1         6907
11093                   H        H         1         6907
11094                   T        T         1         6907
11095                 NaN        L      <NA>         6907
11096                   H        H         1         6907
11097                   H        H         1         6907
11098                 NaN        H      <NA>         6907
11099                   H        L         0         6907
11100                   H        H         1         6907
11101                   H        H         1         6907
11102                   H        H         1         6907
11103                   H        H         1         6907
11104                   H        H         1         6907
1110

In [83]:
top_rows['ss_match'].value_counts()

1    295
0    178
Name: ss_match, dtype: Int64

In [84]:
top_rows['acc_match_RSA'].value_counts()

1.0    552
0.0    448
Name: acc_match_RSA, dtype: int64

In [14]:
gnomad_ss_counts_1 = gnomad_full.loc[(gnomad_full['secondary_structure'] == gnomad_full['ss8_pred']) & (gnomad_full['ss_match'] == 1)].groupby(['secondary_structure', 'ss8_pred']).size().to_dict()

In [15]:
gnomad_ss_counts_1

{('E', 'E'): 987,
 ('G', 'G'): 8,
 ('H', 'H'): 3732,
 ('L', 'L'): 5262,
 ('S', 'S'): 46,
 ('T', 'T'): 298}

In [16]:
gnomad_ss_counts_0 = gnomad_full.loc[(gnomad_full['secondary_structure'] != gnomad_full['ss8_pred']) & (gnomad_full['ss_match'] == 0)].groupby(['secondary_structure', 'ss8_pred']).size().to_dict()

In [17]:
gnomad_ss_counts_0

{('B', 'E'): 20,
 ('B', 'G'): 1,
 ('B', 'H'): 17,
 ('B', 'L'): 39,
 ('B', 'S'): 1,
 ('B', 'T'): 5,
 ('E', 'G'): 4,
 ('E', 'H'): 233,
 ('E', 'L'): 259,
 ('E', 'S'): 7,
 ('E', 'T'): 53,
 ('G', 'E'): 46,
 ('G', 'H'): 132,
 ('G', 'L'): 99,
 ('G', 'S'): 1,
 ('G', 'T'): 42,
 ('H', 'E'): 278,
 ('H', 'G'): 14,
 ('H', 'L'): 384,
 ('H', 'S'): 15,
 ('H', 'T'): 80,
 ('I', 'E'): 4,
 ('I', 'H'): 53,
 ('I', 'L'): 4,
 ('I', 'T'): 4,
 ('L', 'E'): 840,
 ('L', 'G'): 24,
 ('L', 'H'): 937,
 ('L', 'S'): 57,
 ('L', 'T'): 227,
 ('S', 'E'): 144,
 ('S', 'G'): 9,
 ('S', 'H'): 169,
 ('S', 'L'): 446,
 ('S', 'T'): 79,
 ('T', 'E'): 149,
 ('T', 'G'): 11,
 ('T', 'H'): 358,
 ('T', 'L'): 340,
 ('T', 'S'): 23}

In [18]:

gnomad_acc_counts_1 = gnomad_full.loc[(gnomad_full['acc_DSSP'] == gnomad_full['acc_pred']) & (gnomad_full['acc_match'] == 1)].groupby(['acc_DSSP', 'acc_pred']).size().to_dict()
gnomad_acc_counts_0 = gnomad_full.loc[(gnomad_full['acc_DSSP'] != gnomad_full['acc_pred']) & (gnomad_full['acc_match'] == 0)].groupby(['acc_DSSP', 'acc_pred']).size().to_dict()

gnomad_acc2_counts_1 = gnomad_full.loc[(gnomad_full['acc_RSA'] == gnomad_full['acc_pred']) & (gnomad_full['acc_match_RSA'] == 1)].groupby(['acc_RSA', 'acc_pred']).size().to_dict()
gnomad_acc2_counts_0 = gnomad_full.loc[(gnomad_full['acc_RSA'] != gnomad_full['acc_pred']) & (gnomad_full['acc_match_RSA'] == 0)].groupby(['acc_RSA', 'acc_pred']).size().to_dict()


In [19]:
gnomad_acc_counts_1

{('B', 'B'): 2104, ('E', 'E'): 5218, ('M', 'M'): 879}

In [20]:
gnomad_acc_counts_0

{('B', 'E'): 808,
 ('B', 'M'): 777,
 ('E', 'B'): 1346,
 ('E', 'M'): 1172,
 ('M', 'B'): 1211,
 ('M', 'E'): 2426}

In [21]:
gnomad_acc2_counts_1

{('B', 'B'): 1237, ('E', 'E'): 7374, ('M', 'M'): 850}

In [22]:
gnomad_acc2_counts_0

{('B', 'E'): 213,
 ('B', 'M'): 322,
 ('E', 'B'): 2283,
 ('E', 'M'): 1656,
 ('M', 'B'): 1141,
 ('M', 'E'): 865}

### troubleshoot

In [176]:
gnomad_full_less = gnomad_full[0:100]
gnomad_full_less

#CHROM       POS          ID REF ALT      AC         AF      AN     QD  \
0    chr1  11706367  rs11121804   C   T   39444   0.158732  248494  13.47   
1    chr1  11790870   rs2274976   C   T   13949  0.0555184  251250  14.18   
2    chr1  11824498    rs198400   A   G  250947   0.999399  251098  33.49   
3    chr1  11847591      rs5063   C   T   14048  0.0558586  251492  13.96   
4    chr1  11949899   rs7551175   G   A   45490   0.180978  251356  14.94   
..    ...       ...         ...  ..  ..     ...        ...     ...    ...   
95   chr1  15807577  rs61744357   C   T   29649   0.117909  251456     15   
96   chr1  15929149    rs848208   C   T   35413   0.140912  251312  15.73   
97   chr1  15929512    rs848209   T   C  153891   0.615495  250028  24.29   
98   chr1  15933318    rs848210   A   G  154214   0.615635  250496  22.23   
99   chr1  16024780  rs10927887   A   G  138274   0.550726  251076  20.06   

   variant_type                                                vep  \
0         mixed  T|missense_variant|MODERATE|DRAXIN|ENSG0000016...   
1           snv  T|downstream_gene_variant|MODIFIER|C1orf167|EN...   
2           snv  G|missense_variant|MODERATE|CLCN6|ENSG00000011...   
3           snv  T|downstream_gene_variant|MODIFIER|CLCN6|ENSG0...   
4           snv  A|missense_variant|MODERATE|PLOD1|ENSG00000083...   
..          ...                                                ...   
95          snv  T|non_coding_transcript_exon_variant&non_codin...   
96          snv  T|missense_variant|MODERATE|SPEN|ENSG000000655...   
97          snv  C|missense_variant|MODERATE|SPEN|ENSG000000655...   
98    multi-snv  G|missense_variant|MODERATE|SPEN|ENSG000000655...   
99          snv  G|missense_variant|MODERATE|CLCNKA|ENSG0000018...   

                                                flags Allele  \
0    [rf_positive_label, rf_train, segdup, was_mixed]      T   
1   [VQSR_POSITIVE_TRAIN_SITE, rf_positive_label, ...      T   
2   [VQSR_POSITIVE_TRAIN_SITE, rf_positive_label, ...      G   
3   [VQSR_POSITIVE_TRAIN_SITE, rf_positive_label, ...      T   
4   [VQSR_POSITIVE_TRAIN_SITE, rf_positive_label, ...      A   
..                                                ...    ...   
95  [VQSR_POSITIVE_TRAIN_SITE, rf_positive_label, ...      T   
96  [VQSR_POSITIVE_TRAIN_SITE, rf_positive_label, ...      T   
97  [VQSR_POSITIVE_TRAIN_SITE, rf_positive_label, ...      C   
98  [VQSR_POSITIVE_TRAIN_SITE, rf_positive_label, ...      G   
99                                                 []      G   

         Consequence    IMPACT  SYMBOL             Gene Feature_type  \
0   missense_variant  MODERATE  DRAXIN  ENSG00000162490   Transcript   
1   missense_variant  MODERATE   MTHFR  ENSG00000177000   Transcript   
2   missense_variant  MODERATE   CLCN6  ENSG00000011021   Transcript   
3   missense_variant  MODERATE    NPPA  ENSG00000175206   Transcript   
4   missense_variant  MODERATE   PLOD1  ENSG00000083444   Transcript   
..               ...       ...     ...              ...          ...   
95  missense_variant  MODERATE  UQCRHL  ENSG00000233954   Transcript   
96  missense_variant  MODERATE    SPEN  ENSG00000065526   Transcript   
97  missense_variant  MODERATE    SPEN  ENSG00000065526   Transcript   
98  missense_variant  MODERATE    SPEN  ENSG00000065526   Transcript   
99  missense_variant  MODERATE  CLCNKA  ENSG00000186510   Transcript   

            Feature         BIOTYPE   EXON INTRON  HGVSc  HGVSp cDNA_position  \
0   ENST00000294485  protein_coding    2/7    NaN    NaN    NaN      263/7365   
1   ENST00000376590  protein_coding  12/12    NaN    NaN    NaN     1871/7018   
2   ENST00000346436  protein_coding   8/23    NaN    NaN    NaN      665/5589   
3   ENST00000376480  protein_coding    1/3    NaN    NaN    NaN       193/855   
4   ENST00000196061  protein_coding   3/19    NaN    NaN    NaN      358/2976   
..              ...             ...    ...    ...    ...    ...           ...   
95  ENST00000696689  protein_coding 

In [177]:
for item in gnomad_full_less['PDB_path'].unique():
    path = item
    protein = str(path).split("/")[-1].split(".")[0]
    print(path)
    if protein in already_done:
        raptorx_preds = f'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/{protein}/{protein}_PROP/{protein}.all'
    elif protein in new_paths:
        raptorx_preds = f'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/{protein}/{protein}_PROP/{protein}.all'
    else:
        print(f'No RaptorX output for {protein}')
    temp_df = get_raptorx(raptorx_preds)
    for index, row in gnomad_full_less[gnomad_full_less['PDB_path'] == path].iterrows():
        print(index)
        # Access the row data using row['column_name'] or row[column_index]
        # modify the row values directly
        # For example, update a specific column value
        pos = gnomad_full_less['Residue_position'].iloc[index]
        aa = protein_letters_3to1[gnomad_full_less['WT'].iloc[index]]
        match = re.search(r'-F(-?\d+)-', protein)
        if match:
            number = int(match.group(1))
            if number == 1:
                retrieve_data(gnomad_full_less,index,pos,aa)
            else:
                temp_pos = pos-((number-1)*200)
                retrieve_data(gnomad_full_less,index,temp_pos,aa)
        else:
            print(f"No number found for {protein}.")

/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q8NBI3-F1-model_v4.pdb
0
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P42898-F1-model_v4.pdb
1
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P51797-F1-model_v4.pdb
2
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P01160-F1-model_v4.pdb
3
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q02809-F1-model_v4.pdb
4
5
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q5JXC2-F1-model_v4.pdb
6
7
8
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-P20333-F1-model_v4.pdb
9
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_human_v4/AF-Q5THJ4-F5-model_v4.pdb
10
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-Q5VUY0-F1-model_v4.pdb
11
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/AF-O95521-F1-model_v4.pdb
12
13
/ibex/scratch/projects/c2102/databases/alphafold/alphafold_mane/

In [181]:
gnomad_full_less.isnull().sum()

#CHROM                      0
POS                         0
ID                          0
REF                         0
ALT                         0
AC                          0
AF                          0
AN                          0
QD                          0
variant_type                0
vep                         0
flags                       0
Allele                      0
Consequence                 0
IMPACT                      0
SYMBOL                      0
Gene                        0
Feature_type                0
Feature                     0
BIOTYPE                     0
EXON                        0
INTRON                    100
HGVSc                     100
HGVSp                     100
cDNA_position               0
CDS_position                0
Protein_position            0
Amino_acids                 0
Codons                      0
Existing_variation          0
DISTANCE                  100
STRAND                      0
VARIANT_CLASS               0
SYMBOL_SOU

In [182]:
gnomad_full_less

#CHROM       POS            ID REF ALT      AC         AF      AN     QD  \
0    chr1  11706367    rs11121804   C   T   39444   0.158732  248494  13.47   
1    chr1  11790870     rs2274976   C   T   13949  0.0555184  251250  14.18   
2    chr1  11824498      rs198400   A   G  250947   0.999399  251098  33.49   
3    chr1  11847591        rs5063   C   T   14048  0.0558586  251492  13.96   
4    chr1  11949899     rs7551175   G   A   45490   0.180978  251356  14.94   
5    chr1  11950412     rs2273285   G   T   21778  0.0866876  251224  14.57   
6    chr1  12022277    rs11553925   A   T   49896   0.199681  249878  15.72   
7    chr1  12022404    rs11588712   C   T   27588   0.119221  231402  15.28   
8    chr1  12022869     rs2295283   A   G  165360   0.682133  242416  23.34   
9    chr1  12192898     rs1061622   T   G   54148   0.216294  250344  16.18   
10   chr1  12279562     rs4845898   A   T   55150   0.219676  251052  14.49   
11   chr1  12725782    rs11121969   C   T   14579  0.0584929  249244  15.34   
12   chr1  12794279     rs1769774   C   T   77773   0.310838  250204  12.88   
13   chr1  12795729     rs1052908   A   C   50855   0.268197  189618   8.74   
14   chr1  12828511   rs200394590   T   G   28573   0.212483  134472   6.03   
15   chr1  12847526    rs74055698   T   C   40607   0.176483  230090  11.62   
16   chr1  12847643   rs138700801   T   C   12357  0.0503603  245372   8.09   
17   chr1  12847680   rs141872266   T   C   13186   0.053552  246228   8.16   
18   chr1  12859108     rs9661554   G   T   26002    0.10414  249682  12.58   
19   chr1  12859209     rs3204790   T   G   40973    0.16561  247406  15.27   
20   chr1  12859224     rs9659529   C   G   26417   0.105534  250318  14.45   
21   chr1  12859226    rs45443899   C   T   26237   0.104801  250350  14.67   
22   chr1  12859769    rs80027487   C   G   25356   0.101816  249038  14.62   
23   chr1  12860017     rs3204798   T   G   14546  0.0586551  247992  12.16   
24   chr1  12860073    rs72472698   A   G   26776   0.107356  249414  18.69   
25   chr1  12860079     rs3204805   A   G   37919   0.152068  249356  19.38   
26   chr1  12860108    rs72472699   T   G   27437   0.115224  238118  13.49   
27   chr1  12861255    rs12139546   A   G   26356   0.105753  249222  14.12   
28   chr1  12861277    rs12139550   A   G   26362    0.10571  249380  16.38   
29   chr1  12861478    rs56145411   G   A   52774    0.22101  238786  13.28   
30   chr1  12861684     rs1063798   T   G   28394   0.144347  196706   8.59   
31   chr1  12879605    rs28498663   T   C    8288  0.0668937  123898   10.5   
32   chr1  12879619    rs28473210   C   G    9670  0.0744224  129934    9.5   
33   chr1  12879747   rs147865267   C   G   12345  0.0534767  230848  12.11   
34   chr1  12879834    rs74842149   T   G   19270  0.0795334  242288   8.85   
35   chr1  12879843    rs28452936   A   T   26716   0.108431  246386  18.95   
36   chr1  12880083     rs3895133   A   C   19559    0.11264  173642   6.54   
37   chr1  12881902     rs4503360   T   G   12947  0.0609299  212490   5.18   
38   chr1  12881921     rs4514247   G   A   21104  0.0915861  230428  13.71   
39   chr1  12882317     rs3877226   C   G   20155   0.105804  190494   7.51   
40   chr1  12883140     rs4625290   A   C   26576   0.106729  249004   13.8   
41   chr1  12883217     rs3121081   A   C   49484   0.218232  226750  10.74   
42   chr1  12883379     rs3121079   A   G   15309  0.0694891  220308   6.08   
43   chr1  12893425      rs848424   T   C    6734   0.272742   24690  10.42   
44   chr1  12893472     rs4661498   T   C     591  0.0578165   10222  10.13   
45   chr1  12894659   rs149281133   A   G   42924   0.173159  247888   8.45   
46   chr1  12920330   rs113065075   A   G   28407   0.136564  208012  15.34   
47   chr1  12942238             .   T   C     286   0.432024     662  13.24   
48   chr1  12942239             .   G   A     282   0.418398     674  13.86   
49   chr1  12942377  rs1329382820   G   A     487   0

In [186]:

gnomad_full_less['ss_match'] = np.where(gnomad_full_less['secondary_structure'].equals(gnomad_full_less['ss8_pred']), 1, 0)


<ipython-input-186-af90164ab8ba>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gnomad_full_less['ss_match'] = np.where(gnomad_full_less['secondary_structure'].equals(gnomad_full_less['ss8_pred']), 1, 0)


In [190]:
gnomad_full_less['ss_match'] = np.where((gnomad_full_less['secondary_structure'] == gnomad_full_less['ss8_pred'])
                                        & (~gnomad_full_less['secondary_structure'].isnull())
                                        & (~gnomad_full_less['ss8_pred'].isnull()), 1,
                                        np.where(gnomad_full_less['secondary_structure'].isnull()
                                                 | gnomad_full_less['ss8_pred'].isnull(), np.nan, 0))

<ipython-input-190-5aa9eec28a3d>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gnomad_full_less['ss_match'] = np.where((gnomad_full_less['secondary_structure'] == gnomad_full_less['ss8_pred'])


In [193]:
gnomad_full_less['ss_match'] = gnomad_full_less['ss_match'].astype('Int64')

<ipython-input-193-07f02b8a00a7>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gnomad_full_less['ss_match'] = gnomad_full_less['ss_match'].astype('Int64')


In [189]:
gnomad_full_less['secondary_structure']==gnomad_full_less['ss8_pred']

0     False
1     False
2     False
3     False
4      True
5     False
6     False
7     False
8     False
9     False
10    False
11    False
12     True
13     True
14    False
15    False
16    False
17     True
18     True
19    False
20    False
21    False
22    False
23    False
24     True
25     True
26    False
27    False
28     True
29    False
30     True
31    False
32     True
33    False
34    False
35    False
36    False
37    False
38    False
39    False
40     True
41    False
42    False
43    False
44    False
45    False
46     True
47    False
48    False
49    False
50     True
51    False
52    False
53    False
54    False
55    False
56    False
57    False
58    False
59     True
60     True
61     True
62     True
63    False
64     True
65     True
66    False
67    False
68     True
69     True
70     True
71    False
72    False
73    False
74    False
75    False
76     True
77    False
78    False
79    False
80     True
81    False
82    False
83  

In [196]:
gnomad_full_less[['secondary_structure','ss8_pred','ss_match']]

secondary_structure ss8_pred  ss_match
0                  NaN        L      <NA>
1                    I        H         0
2                    B        H         0
3                  NaN        L      <NA>
4                    E        E         1
5                    T        H         0
6                  NaN        L      <NA>
7                  NaN        L      <NA>
8                    T        L         0
9                    B        E         0
10                 NaN        L      <NA>
11                 NaN        L      <NA>
12                   H        H         1
13                   T        T         1
14                 NaN        T      <NA>
15                 NaN        L      <NA>
16                   T        L         0
17                   H        H         1
18                   H        H         1
19                   T        H         0
20                   G        H         0
21                 NaN        T      <NA>
22                   T        E         0
23                   G        E         0
24                   H        H         1
25                   H        H         1
26                 NaN        H      <NA>
27                   E        L         0
28                   H        H         1
29                   T        E         0
30                   H        H         1
31                 NaN        L      <NA>
32                   E        E         1
33                   E        H         0
34                 NaN        L      <NA>
35                   T        H         0
36                   E        H         0
37                   E        H         0
38                   T        H         0
39                 NaN        G      <NA>
40                   H        H         1
41                   T        H         0
42                 NaN        L      <NA>
43                 NaN        L      <NA>
44                   T        H         0
45                 NaN        E      <NA>
46                   E        E         1
47                 NaN        L      <NA>
48                 NaN        L      <NA>
49                 NaN        H      <NA>
50                   H        H         1
51                 NaN        L      <NA>
52                 NaN        L      <NA>
53                 NaN        L      <NA>
54                 NaN        L      <NA>
55                 NaN        L      <NA>
56                   E        L         0
57                   E        H         0
58                   T        H         0
59                   H        H         1
60                   H        H         1
61                   H        H         1
62                   H        H         1
63                 NaN        L      <NA>
64                   H        H         1
65                   H        H         1
66                   G        L         0
67                 NaN        T      <NA>
68                   H        H         1
69                   H        H         1
70                   H        H         1
71                 NaN        L      <NA>
72                   G        T         0
73                 NaN        L      <NA>
74                 NaN        L      <NA>
75                 NaN        H      <NA>
76                   H        H         1
77                   T        H         0
78                 NaN        T      <NA>
79                 NaN        L      <NA>
80                   H        H         1
81                 NaN        L      <NA>
82                 NaN        L      <NA>
83                 NaN        S      <NA>
84                   G        H         0
85                   E        L         0
86                   H        H         1
87                   H        H         1
88                   H        H         1
89                 NaN        E      <NA>
90                 NaN        H      <NA>
91                 NaN        S      <NA>
92                 NaN        H      <NA>
93                 NaN        L      <NA>
94           

In [197]:
gnomad_full_less['ss_match'].value_counts()

1    29
0    28
Name: ss_match, dtype: Int64

In [199]:
sorted(gnomad_expanded['accessibility'].value_counts())

[1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 2,
 2,
 3,
 3,
 4,
 5,
 6,
 6,
 7,
 8,
 9,
 9,
 9,
 10,
 11,
 11,
 12,
 13,
 13,
 14,
 14,
 14,
 14,
 14,
 14,
 15,
 15,
 15,
 16,
 16,
 16,
 17,
 17,
 17,
 17,
 17,
 17,
 17,
 17,
 18,
 18,
 18,
 18,
 19,
 19,
 19,
 19,
 19,
 19,
 19,
 20,
 20,
 20,
 20,
 21,
 21,
 21,
 21,
 22,
 22,
 23,
 23,
 23,
 24,
 24,
 28,
 28,
 30,
 30,
 31,
 31,
 31,
 32,
 35,
 36,
 37,
 37,
 37,
 37,
 39,
 40,
 41,
 41,
 42,
 42,
 43,
 44,
 45,
 47,
 47,
 47,
 48,
 48,
 49,
 50,
 51,
 51,
 51,
 52,
 52,
 53,
 53,
 54,
 54,
 54,
 54,
 54,
 55,
 55,
 55,
 56,
 56,
 56,
 56,
 57,
 57,
 57,
 57,
 58,
 58,
 58,
 59,
 59,
 59,
 59,
 60,
 60,
 60,
 60,
 60,
 60,
 60,
 61,
 61,
 62,
 62,
 62,
 62,
 63,
 63,
 63,
 64,
 64,
 64,
 64,
 64,
 64,
 65,
 65,
 65,
 66,
 66,
 66,
 66,
 66,
 67,
 67,
 68,
 68,
 69,
 69,
 69,
 69,
 69,
 70,
 70,
 70,
 70,
 70,
 71,
 72,
 72,
 73,
 73,
 74,
 75,
 75,
 77,
 77,
 78,
 79,
 80,
 81,
 81,
 81,
 83,
 84,
 84,
 85,
 85,
 86,
 87,
 88,
 88,
 88,
 8

In [213]:
def assign_access_letter(access):
    if access <= 50:
        return 'B'
    elif access <= 100:
        return 'M'
    else:
        return 'E'

gnomad_full_less['acc_letter'] = gnomad_full_less['accessibility'].apply(assign_access_letter)

In [214]:
gnomad_full_less['acc_match'] = np.where((gnomad_full_less['acc_letter'] == gnomad_full_less['acc_pred'])
                                        & (~gnomad_full_less['acc_letter'].isnull())
                                        & (~gnomad_full_less['acc_pred'].isnull()), 1,
                                        np.where(gnomad_full_less['acc_letter'].isnull()
                                                 | gnomad_full_less['acc_pred'].isnull(), np.nan, 0))

In [215]:
gnomad_full_less[['acc_letter','acc_pred','acc_match']]

acc_letter acc_pred  acc_match
0           E        B        0.0
1           B        M        0.0
2           B        E        0.0
3           M        B        0.0
4           B        B        1.0
5           B        B        1.0
6           E        E        1.0
7           E        E        1.0
8           E        E        1.0
9           E        B        0.0
10          E        E        1.0
11          B        E        0.0
12          B        E        0.0
13          E        E        1.0
14          M        E        0.0
15          E        E        1.0
16          E        E        1.0
17          M        E        0.0
18          E        M        0.0
19          B        B        1.0
20          M        E        0.0
21          B        M        0.0
22          E        B        0.0
23          B        B        1.0
24          B        M        0.0
25          B        M        0.0
26          B        B        1.0
27          B        M        0.0
28          E        E        1.0
29          M        B        0.0
30          M        M        1.0
31          E        B        0.0
32          B        B        1.0
33          B        E        0.0
34          M        M        1.0
35          E        B        0.0
36          B        B        1.0
37          B        B        1.0
38          E        M        0.0
39          E        E        1.0
40          M        E        0.0
41          B        E        0.0
42          E        B        0.0
43          M        M        1.0
44          M        M        1.0
45          B        B        1.0
46          E        B        0.0
47          M        E        0.0
48          M        E        0.0
49          E        M        0.0
50          M        E        0.0
51          E        E        1.0
52          M        E        0.0
53          E        E        1.0
54          E        E        1.0
55          E        E        1.0
56          B        B        1.0
57          M        B        0.0
58          E        B        0.0
59          B        B        1.0
60          B        B        1.0
61          M        E        0.0
62          E        B        0.0
63          E        E        1.0
64          B        B        1.0
65          B        B        1.0
66          M        E        0.0
67          E        E        1.0
68          M        M        1.0
69          E        E        1.0
70          B        M        0.0
71          M        M        1.0
72          E        M        0.0
73          B        E        0.0
74          B        M        0.0
75          E        E        1.0
76          B        B        1.0
77          B        B        1.0
78          M        E        0.0
79          E        E        1.0
80          M        E        0.0
81          E        E        1.0
82          E        E        1.0
83          B        M        0.0
84          E        E        1.0
85          M        M        1.0
86          E        M        0.0
87          B        M        0.0
88          M        M        1.0
89          B        B        1.0
90          E        B        0.0
91          M        B        0.0
92          E        M        0.0
93          B        M        0.0
94          M        B        0.0
95          E        E        1.0
96          M        E        0.0
97          E        B        0.0
98          E        E        1.0
99          E        E        1.0

In [220]:
gnomad_full_less['acc_match'].value_counts()

0.0    51
1.0    49
Name: acc_match, dtype: int64

In [216]:
maxasa_dict = {
    'A': 113,
    'R': 241,
    'N': 158,
    'D': 151,
    'C': 140,
    'E': 183,
    'Q': 189,
    'G': 85,
    'H': 194,
    'I': 182,
    'L': 180,
    'K': 211,
    'M': 204,
    'F': 218,
    'P': 143,
    'S': 122,
    'T': 146,
    'W': 259,
    'Y': 229,
    'V': 160
}

In [231]:
gnomad_full_less['WT'] = gnomad_full_less['WT'].map(protein_letters_3to1)

In [232]:
gnomad_full_less['MUT'] = gnomad_full_less['MUT'].map(protein_letters_3to1)

In [239]:
gnomad_full_less['RSA'] = (gnomad_full_less['accessibility'] / gnomad_full_less['WT'].map(maxasa_dict))*100

In [230]:
gnomad_full_less['WT'].iloc[2]

'Glu'

In [274]:
def assign_acc(access):
    if access <= 12:
        return 'B'
    elif access <= 42:
        return 'M'
    else:
        return 'E'

gnomad_full_less['acc_letter_2'] = gnomad_full_less['RSA'].apply(assign_acc)

In [275]:
gnomad_full_less['acc_match_2'] = np.where((gnomad_full_less['acc_letter_2'] == gnomad_full_less['acc_pred'])
                                        & (~gnomad_full_less['acc_letter_2'].isnull())
                                        & (~gnomad_full_less['acc_pred'].isnull()), 1,
                                        np.where(gnomad_full_less['acc_letter_2'].isnull()
                                                 | gnomad_full_less['acc_pred'].isnull(), np.nan, 0))

In [251]:
gnomad_full_less[['acc_letter_2','acc_pred','acc_match_2']]

acc_letter_2 acc_pred  acc_match_2
0             E        B          0.0
1             M        M          1.0
2             B        E          0.0
3             E        B          0.0
4             B        B          1.0
5             E        B          0.0
6             E        E          1.0
7             E        E          1.0
8             E        E          1.0
9             E        B          0.0
10            E        E          1.0
11            M        E          0.0
12            M        E          0.0
13            E        E          1.0
14            E        E          1.0
15            E        E          1.0
16            E        E          1.0
17            E        E          1.0
18            E        M          0.0
19            B        B          1.0
20            E        E          1.0
21            M        M          1.0
22            E        B          0.0
23            M        B          0.0
24            M        M          1.0
25            M        M          1.0
26            M        B          0.0
27            B        M          0.0
28            E        E          1.0
29            E        B          0.0
30            E        M          0.0
31            E        B          0.0
32            M        B          0.0
33            M        E          0.0
34            E        M          0.0
35            E        B          0.0
36            M        B          0.0
37            M        B          0.0
38            E        M          0.0
39            E        E          1.0
40            E        E          1.0
41            M        E          0.0
42            E        B          0.0
43            E        M          0.0
44            M        M          1.0
45            M        B          0.0
46            E        B          0.0
47            E        E          1.0
48            E        E          1.0
49            E        M          0.0
50            E        E          1.0
51            E        E          1.0
52            E        E          1.0
53            E        E          1.0
54            E        E          1.0
55            E        E          1.0
56            M        B          0.0
57            M        B          0.0
58            E        B          0.0
59            M        B          0.0
60            B        B          1.0
61            E        E          1.0
62            E        B          0.0
63            E        E          1.0
64            M        B          0.0
65            M        B          0.0
66            E        E          1.0
67            E        E          1.0
68            E        M          0.0
69            E        E          1.0
70            B        M          0.0
71            E        M          0.0
72            E        M          0.0
73            M        E          0.0
74            E        M          0.0
75            E        E          1.0
76            E        B          0.0
77            B        B          1.0
78            E        E          1.0
79            E        E          1.0
80            E        E          1.0
81            E        E          1.0
82            E        E          1.0
83            M        M          1.0
84            E        E          1.0
85            M        M          1.0
86            E        M          0.0
87            M        M          1.0
88            E        M          0.0
89            E        B          0.0
90            E        B          0.0
91            E        B          0.0
92            E        M          0.0
93            E        M          0.0
94            E        B          0.0
95            E        E          1.0
96            E        E          1.0
97            E        B          0.0
98            E        E          1.0
99            E        E          1.0

In [243]:
gnomad_full_less['RSA']

0      80.000000
1      11.203320
2       2.732240
3      47.500000
4       0.000000
5      35.398230
6      91.469194
7      78.321678
8      91.469194
9      59.313725
10     88.524590
11     17.482517
12     22.377622
13     57.261411
14     42.857143
15     84.768212
16     70.142180
17     45.054945
18     56.016598
19      0.000000
20     52.739726
21     13.333333
22     91.666667
23     13.736264
24     22.274882
25     17.030568
26     31.428571
27      4.109589
28     56.284153
29     48.571429
30     43.119266
31     54.148472
32      8.333333
33     24.375000
34     41.772152
35     49.541284
36     22.018349
37     21.397380
38     77.593361
39    106.010929
40     48.344371
41     13.114754
42     84.169884
43     39.726027
44     33.624454
45     19.285714
46     56.043956
47     47.938144
48     47.938144
49     48.962656
50     66.393443
51     89.041096
52     78.688525
53     80.379747
54     89.873418
55     83.505155
56     13.698630
57     26.637555
58     55.1546

In [276]:
gnomad_full_less['acc_match_2'].value_counts()

1.0    52
0.0    48
Name: acc_match_2, dtype: int64

In [141]:
def retrieve_data(df,index,pos,aa):
    if (temp_df['position'].iloc[pos-1] == pos) & (temp_df['AA'].iloc[pos-1] == aa):
        for column in column_names:
            df.at[index, column] = temp_df[column].iloc[pos-1]

In [156]:
def get_raptorx(file_path):
    
    # Read the file
    with open(file_path, 'r') as file:
        file_content = file.read()
        
    # Extract SS8 predictions
    ss8_start = file_content.find('#---------------- details of SS8 prediction ---------------------------')
    ss8_end = file_content.find('#---------------- details of ACC prediction ---------------------------')
    ss8_lines = file_content[ss8_start: ss8_end]  
    #print(ss8_lines)
    # Extract ACC predictions
    acc_start = file_content.find('#---------------- details of ACC prediction ---------------------------')
    acc_end = file_content.find('#---------------- details of DISO prediction --------------------------')
    acc_lines = file_content[acc_start: acc_end]
    # Extract DISO predictions
    diso_start = file_content.find('#---------------- details of DISO prediction --------------------------')
    diso_end = file_content.find('#---------------- details of TM2 prediction ---------------------------')
    diso_lines = file_content[diso_start: diso_end]
    # Extract TM8 predictions
    tm8_start = file_content.find('#---------------- details of TM8 prediction ---------------------------')
    tm8_end = len(file_content)
    tm8_lines = file_content[tm8_start:tm8_end]
        
    # Create a ss8 DataFrame from the lines
    ss8_columns = ['position', 'AA','ss8_pred','ss8_H','ss8_G','ss8_I','ss8_E','ss8_B','ss8_T','ss8_S','ss8_L']
    ss8_rows = [line.strip() for line in ss8_lines.split('\n') if not line.startswith('#')]
    ss8_values = [row.split() for row in ss8_rows]
    data_ss8 = pd.DataFrame(ss8_values, columns=ss8_columns)
    data_ss8.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = ss8_columns[3:]
    pos_column = ss8_columns[0]
    data_ss8[numeric_columns] = data_ss8[numeric_columns].astype(float)
    data_ss8[pos_column] = data_ss8[pos_column].astype(int)
    
    # Create an acc DataFrame from the lines
    acc_columns = ['position', 'AA','acc_pred','acc_B','acc_M','acc_E']
    acc_rows = [line.strip() for line in acc_lines.split('\n') if not line.startswith('#')]
    acc_values = [row.split() for row in acc_rows]
    data_acc = pd.DataFrame(acc_values, columns=acc_columns)
    data_acc.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = acc_columns[3:]
    pos_column = acc_columns[0]
    data_acc[numeric_columns] = data_acc[numeric_columns].astype(float)
    data_acc[pos_column] = data_acc[pos_column].astype(int)
    
    # Create an diso DataFrame from the lines
    diso_columns = ['position', 'AA','diso_pred','diso_score']
    diso_rows = [line.strip() for line in diso_lines.split('\n') if not line.startswith('#')]
    diso_values = [row.split() for row in diso_rows]
    data_diso = pd.DataFrame(diso_values, columns=diso_columns)
    data_diso.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = diso_columns[3:]
    pos_column = diso_columns[0]
    data_diso[numeric_columns] = data_diso[numeric_columns].astype(float)
    data_diso[pos_column] = data_diso[pos_column].astype(int)
    
    # Create an acc DataFrame from the lines
    tm8_columns = ['position', 'AA','tm8_pred','tm8_H','tm8_E','tm8_C','tm8_I','tm8_L','tm8_F','tm8_X','tm8__']
    tm8_rows = [line.strip() for line in tm8_lines.split('\n') if not line.startswith('#')]
    tm8_values = [row.split() for row in tm8_rows]
    data_tm8 = pd.DataFrame(tm8_values, columns=tm8_columns)
    data_tm8.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = tm8_columns[3:]
    pos_column = tm8_columns[0]
    data_tm8[numeric_columns] = data_tm8[numeric_columns].astype(float)
    data_tm8[pos_column] = data_tm8[pos_column].astype(int)

    # Optionally, you can set column names
    big_df = pd.DataFrame()
    if all(df['position'].equals(data_ss8['position']) and df['AA'].equals(data_ss8['AA']) for df in [data_acc, data_diso, data_tm8]):
        # If the columns are equal, keep only one copy at the beginning of big_df
        big_df = pd.concat([data_ss8, data_acc.iloc[:, 2:], data_diso.iloc[:, 2:], data_tm8.iloc[:, 2:]], axis=1)
    else:
        # If the columns are not equal, concatenate all dataframes as usual
        print(f'Positions and AAs do not match between data_ss8, data_acc, data_diso, data_tm8 of {file_path}.')
        big_df = pd.concat([data_ss8, data_acc, data_diso, data_tm8], axis=1)
        
    #column_names = ['position', 'AA','ss_H','ss_G','ss_I','ss_E','ss_B','ss_T','ss_S','ss_L','acc_B','acc_M','acc_E','diso_score','tm8_H','tm8_E','tm8_C','tm8_I','tm8_L','tm8_F','tm8_X','tm8__']  # Replace with your actual column names
    #big_df.columns = column_names

    # Create a DataFrame from the extracted data
    return big_df

In [157]:
big_df = get_raptorx('/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/AF-Q9BYI3-F1-model_v4/AF-Q9BYI3-F1-model_v4_PROP/AF-Q9BYI3-F1-model_v4.all')

In [129]:
data_ss8

position AA pred   ss_H   ss_G   ss_I   ss_E   ss_B   ss_T   ss_S   ss_L
0           1  M    L  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.999
1           2  F    L  0.008  0.001  0.001  0.027  0.016  0.009  0.002  0.936
2           3  T    L  0.021  0.003  0.000  0.033  0.014  0.012  0.041  0.876
3           4  S    L  0.057  0.013  0.000  0.019  0.010  0.046  0.096  0.758
4           5  E    L  0.256  0.022  0.000  0.012  0.005  0.172  0.073  0.460
..        ... ..  ...    ...    ...    ...    ...    ...    ...    ...    ...
516       517  T    E  0.030  0.003  0.000  0.614  0.004  0.007  0.010  0.332
517       518  L    E  0.019  0.004  0.000  0.477  0.004  0.005  0.016  0.474
518       519  S    L  0.006  0.002  0.000  0.278  0.004  0.006  0.025  0.679
519       520  T    L  0.001  0.002  0.000  0.097  0.002  0.005  0.002  0.891
520       521  D    L  0.000  0.000  0.000  0.001  0.000  0.000  0.000  0.999

[521 rows x 11 columns]

In [121]:
data_acc

position AA pred  acc_B  acc_M  acc_E
0           1  M    E  0.009  0.047  0.944
1           2  F    E  0.124  0.161  0.716
2           3  T    E  0.155  0.203  0.643
3           4  S    E  0.123  0.239  0.638
4           5  E    E  0.099  0.262  0.639
..        ... ..  ...    ...    ...    ...
516       517  T    E  0.086  0.235  0.678
517       518  L    B  0.571  0.138  0.291
518       519  S    E  0.081  0.261  0.658
519       520  T    E  0.092  0.093  0.815
520       521  D    E  0.001  0.017  0.981

[521 rows x 6 columns]

In [122]:
data_diso

position AA pred  diso_score
0           1  M    *       0.995
1           2  F    *       0.974
2           3  T    *       0.901
3           4  S    *       0.796
4           5  E    *       0.608
..        ... ..  ...         ...
516       517  T    .       0.304
517       518  L    .       0.426
518       519  S    *       0.681
519       520  T    *       0.928
520       521  D    *       0.992

[521 rows x 4 columns]

In [123]:
data_tm8

position AA pred  tm8_H  tm8_E  tm8_C  tm8_I  tm8_L  tm8_F  tm8_X  tm8__
0           1  M    X  0.016  0.002  0.002  0.055  0.010  0.013  0.646  0.256
1           2  F    X  0.006  0.001  0.000  0.033  0.002  0.008  0.661  0.288
2           3  T    X  0.002  0.001  0.000  0.021  0.001  0.006  0.663  0.305
3           4  S    X  0.002  0.002  0.000  0.017  0.001  0.008  0.657  0.312
4           5  E    X  0.003  0.004  0.000  0.017  0.002  0.012  0.645  0.316
..        ... ..  ...    ...    ...    ...    ...    ...    ...    ...    ...
516       517  T    E  0.002  0.379  0.001  0.036  0.004  0.005  0.327  0.246
517       518  L    E  0.001  0.375  0.000  0.030  0.002  0.003  0.335  0.254
518       519  S    E  0.001  0.363  0.000  0.024  0.001  0.001  0.338  0.272
519       520  T    E  0.001  0.346  0.000  0.023  0.001  0.001  0.338  0.290
520       521  D    X  0.004  0.327  0.002  0.032  0.005  0.004  0.331  0.296

[521 rows x 11 columns]

In [158]:
big_df

position AA ss8_pred  ss8_H  ss8_G  ss8_I  ss8_E  ss8_B  ss8_T  ss8_S  \
0           1  M        L  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
1           2  F        L  0.008  0.001  0.001  0.027  0.016  0.009  0.002   
2           3  T        L  0.021  0.003  0.000  0.033  0.014  0.012  0.041   
3           4  S        L  0.057  0.013  0.000  0.019  0.010  0.046  0.096   
4           5  E        L  0.256  0.022  0.000  0.012  0.005  0.172  0.073   
..        ... ..      ...    ...    ...    ...    ...    ...    ...    ...   
516       517  T        E  0.030  0.003  0.000  0.614  0.004  0.007  0.010   
517       518  L        E  0.019  0.004  0.000  0.477  0.004  0.005  0.016   
518       519  S        L  0.006  0.002  0.000  0.278  0.004  0.006  0.025   
519       520  T        L  0.001  0.002  0.000  0.097  0.002  0.005  0.002   
520       521  D        L  0.000  0.000  0.000  0.001  0.000  0.000  0.000   

     ss8_L acc_pred  acc_B  acc_M  acc_E diso_pred  diso_score tm8_pred  \
0    0.999        E  0.009  0.047  0.944         *       0.995        X   
1    0.936        E  0.124  0.161  0.716         *       0.974        X   
2    0.876        E  0.155  0.203  0.643         *       0.901        X   
3    0.758        E  0.123  0.239  0.638         *       0.796        X   
4    0.460        E  0.099  0.262  0.639         *       0.608        X   
..     ...      ...    ...    ...    ...       ...         ...      ...   
516  0.332        E  0.086  0.235  0.678         .       0.304        E   
517  0.474        B  0.571  0.138  0.291         .       0.426        E   
518  0.679        E  0.081  0.261  0.658         *       0.681        E   
519  0.891        E  0.092  0.093  0.815         *       0.928        E   
520  0.999        E  0.001  0.017  0.981         *       0.992        X   

     tm8_H  tm8_E  tm8_C  tm8_I  tm8_L  tm8_F  tm8_X  tm8__  
0    0.016  0.002  0.002  0.055  0.010  0.013  0.646  0.256  
1    0.006  0.001  0.000  0.033  0.002  0.008  0.661  0.288  
2    0.002  0.001  0.000  0.021  0.001  0.006  0.663  0.305  
3    0.002  0.002  0.000  0.017  0.001  0.008  0.657  0.312  
4    0.003  0.004  0.000  0.017  0.002  0.012  0.645  0.316  
..     ...    ...    ...    ...    ...    ...    ...    ...  
516  0.002  0.379  0.001  0.036  0.004  0.005  0.327  0.246  
517  0.001  0.375  0.000  0.030  0.002  0.003  0.335  0.254  
518  0.001  0.363  0.000  0.024  0.001  0.001  0.338  0.272  
519  0.001  0.346  0.000  0.023  0.001  0.001  0.338  0.290  
520  0.004  0.327  0.002  0.032  0.005  0.004  0.331  0.296  

[521 rows x 26 columns]

In [4]:
gnomad_full = pd.read_pickle('gnomad_full.pkl')

In [5]:
gnomad_full

#CHROM       POS            ID REF ALT      AC         AF      AN  \
0       chr1  11706367    rs11121804   C   T   39444   0.158732  248494   
1       chr1  11790870     rs2274976   C   T   13949  0.0555184  251250   
2       chr1  11824498      rs198400   A   G  250947   0.999399  251098   
3       chr1  11847591        rs5063   C   T   14048  0.0558586  251492   
4       chr1  11949899     rs7551175   G   A   45490   0.180978  251356   
...      ...       ...           ...  ..  ..     ...        ...     ...   
15936   chrX  72140250     rs7061150   C   T   12196  0.0674621  180783   
15937   chrY   6246522   rs201475959   A   G    1025  0.0780952   13125   
15938   chrY  12720687     rs7067496   G   T    6033  0.0894759   67426   
15939   chrY  22180292  rs1478920645   G   T       1   0.142857       7   
15940   chrY  22406127  rs1195699969   C   A       9          1       9   

          QD variant_type  ...  tm8_L  tm8_F  tm8_X  tm8__ acc_DSSP  \
0      13.47        mixed  ...  0.001  0.005  0.334  0.649        E   
1      14.18          snv  ...  0.014  0.024  0.219  0.639        B   
2      33.49          snv  ...  0.005   0.01  0.014  0.796        B   
3      13.96          snv  ...  0.005  0.011  0.121  0.825        M   
4      14.94          snv  ...  0.013  0.022  0.059  0.734        B   
...      ...          ...  ...    ...    ...    ...    ...      ...   
15936  19.16          snv  ...  0.008  0.013  0.346  0.435        E   
15937  30.14          snv  ...  0.003  0.007  0.315  0.658        E   
15938  32.95          snv  ...  0.002  0.005  0.815  0.165        M   
15939  15.53          snv  ...  0.002  0.006   0.37  0.573        B   
15940  24.33          snv  ...  0.002  0.006   0.37  0.573        B   

             RSA acc_RSA acc_match acc_match_RSA ss_match  
0      80.000000       E       0.0           0.0        1  
1      11.203320       B       0.0           0.0        0  
2       2.732240       B       0.0           0.0        0  
3      47.500000       E       0.0           0.0        1  
4       0.000000       B       1.0           1.0        1  
...          ...     ...       ...           ...      ...  
15936  91.780822       E       1.0           1.0        1  
15937  69.398907       E       1.0           1.0        1  
15938  51.366120       E       0.0           1.0        1  
15939  30.821918       M       0.0           0.0        1  
15940  30.821918       M       0.0           0.0        1  

[15941 rows x 146 columns]

In [26]:
column_names = ['ss3_pred','ss3_H','ss3_E','ss3_C']

# Add new columns to the dataframe with no values
gnomad_full[column_names] = pd.DataFrame(columns=column_names)

In [27]:
def retrieve_data(df,index,pos,aa):
    if (temp_df['position'].iloc[pos-1] == pos) & (temp_df['AA'].iloc[pos-1] == aa):
        for column in column_names:
            df.at[index, column] = temp_df[column].iloc[pos-1]

In [20]:
def get_ss3(file_path):
    
    # Read the file
    with open(file_path, 'r') as file:
        file_content = file.read()
        
    # Extract SS3 predictions
    ss3_start = file_content.find('#---------------- details of SS3 prediction ---------------------------')
    ss3_end = file_content.find('#---------------- details of SS8 prediction ---------------------------')
    ss3_lines = file_content[ss3_start: ss3_end]  
    #print(ss8_lines)
    
        
    # Create a ss8 DataFrame from the lines
    ss3_columns = ['position', 'AA','ss3_pred','ss3_H','ss3_E','ss3_C']
    ss3_rows = [line.strip() for line in ss3_lines.split('\n') if not line.startswith('#')]
    ss3_values = [row.split() for row in ss3_rows]
    data_ss3 = pd.DataFrame(ss3_values, columns=ss3_columns)
    data_ss3.dropna(how='all', inplace=True)
    # Convert numeric columns to float
    numeric_columns = ss3_columns[3:]
    pos_column = ss3_columns[0]
    data_ss3[numeric_columns] = data_ss3[numeric_columns].astype(float)
    data_ss3[pos_column] = data_ss3[pos_column].astype(int)

    # Optionally, you can set column names
    big_df = pd.DataFrame()
    big_df = data_ss3
        
    #column_names = ['position', 'AA','ss_H','ss_G','ss_I','ss_E','ss_B','ss_T','ss_S','ss_L','acc_B','acc_M','acc_E','diso_score','tm8_H','tm8_E','tm8_C','tm8_I','tm8_L','tm8_F','tm8_X','tm8__']  # Replace with your actual column names
    #big_df.columns = column_names

    # Create a DataFrame from the extracted data
    return big_df

In [28]:
for item in gnomad_full['PDB_path'].unique():
    path = item
    protein = str(path).split("/")[-1].split(".")[0]
    if protein in already_done:
        raptorx_preds = f'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/{protein}/{protein}_PROP/{protein}.all'
    elif protein in new_paths:
        raptorx_preds = f'/ibex/scratch/penaguka/run_pipeline/variant_annotator/notebooks/raptorXoutputs/gnomad/{protein}/{protein}_PROP/{protein}.all'
    else:
        print(f'No RaptorX output for {protein}')
    temp_df = get_ss3(raptorx_preds)
    for index, row in gnomad_full[gnomad_full['PDB_path'] == path].iterrows():
        #print(index)
        # Access the row data using row['column_name'] or row[column_index]
        # modify the row values directly
        # For example, update a specific column value
        pos = gnomad_full['Residue_position'].iloc[index]
        aa = gnomad_full['WT'].iloc[index]
        match = re.search(r'-F(-?\d+)-', protein)
        if match:
            number = int(match.group(1))
            if number == 1:
                retrieve_data(gnomad_full,index,pos,aa)
            else:
                temp_pos = pos-((number-1)*200)
                retrieve_data(gnomad_full,index,temp_pos,aa)
        else:
            print(f"No number found for {protein}.")

In [29]:
gnomad_full.to_pickle('gnomad_full_ss3.pkl')

In [30]:
gnomad_full

#CHROM       POS            ID REF ALT      AC         AF      AN  \
0       chr1  11706367    rs11121804   C   T   39444   0.158732  248494   
1       chr1  11790870     rs2274976   C   T   13949  0.0555184  251250   
2       chr1  11824498      rs198400   A   G  250947   0.999399  251098   
3       chr1  11847591        rs5063   C   T   14048  0.0558586  251492   
4       chr1  11949899     rs7551175   G   A   45490   0.180978  251356   
5       chr1  11950412     rs2273285   G   T   21778  0.0866876  251224   
6       chr1  12022277    rs11553925   A   T   49896   0.199681  249878   
7       chr1  12022404    rs11588712   C   T   27588   0.119221  231402   
8       chr1  12022869     rs2295283   A   G  165360   0.682133  242416   
9       chr1  12192898     rs1061622   T   G   54148   0.216294  250344   
10      chr1  12279562     rs4845898   A   T   55150   0.219676  251052   
11      chr1  12725782    rs11121969   C   T   14579  0.0584929  249244   
12      chr1  12794279     rs1769774   C   T   77773   0.310838  250204   
13      chr1  12795729     rs1052908   A   C   50855   0.268197  189618   
14      chr1  12828511   rs200394590   T   G   28573   0.212483  134472   
15      chr1  12847526    rs74055698   T   C   40607   0.176483  230090   
16      chr1  12847643   rs138700801   T   C   12357  0.0503603  245372   
17      chr1  12847680   rs141872266   T   C   13186   0.053552  246228   
18      chr1  12859108     rs9661554   G   T   26002    0.10414  249682   
19      chr1  12859209     rs3204790   T   G   40973    0.16561  247406   
20      chr1  12859224     rs9659529   C   G   26417   0.105534  250318   
21      chr1  12859226    rs45443899   C   T   26237   0.104801  250350   
22      chr1  12859769    rs80027487   C   G   25356   0.101816  249038   
23      chr1  12860017     rs3204798   T   G   14546  0.0586551  247992   
24      chr1  12860073    rs72472698   A   G   26776   0.107356  249414   
...      ...       ...           ...  ..  ..     ...        ...     ...   
15916   chrX  50376086     rs4074320   C   T   41414   0.231714  178729   
15917   chrX  50911091    rs41308602   A   G    7747  0.0570719  135741   
15918   chrX  52645464   rs112382781   G   T   16845  0.0979064  172052   
15919   chrX  54755097    rs17316491   C   G   11594  0.0642555  180436   
15920   chrX  54925031    rs45448595   C   T   10765  0.0596419  180494   
15921   chrX  55090033     rs1845444   C   G  177865   0.979125  181657   
15922   chrX  55263341     rs4826381   T   C  169359   0.933792  181367   
15923   chrX  55624568     rs2375465   T   C  170097   0.934383  182042   
15924   chrX  57136462     rs2003812   G   A   41123    0.93108   44167   
15925   chrX  57592412   rs199513692   G   A    4161   0.050147   82976   
15926   chrX  57592416   rs200267267   A   C    4385  0.0567322   77293   
15927   chrX  57592437   rs189164178   G   A   10971   0.168288   65192   
15928   chrX  66602765     rs1385698   T   C  149078   0.980931  151976   
15929   chrX  66605144     rs1385699   C   T  140733   0.793474  177363   
15930   chrX  68432906    rs41303733   C   T   10488  0.0572795  183102   
15931   chrX  69505797     rs1171942   T   C   89348   0.492984  181239   
15932   chrX  70258925     rs3829709   A   C   20562   0.114082  180239   
15933   chrX  70259092     rs1152187   T   G   42510   0.232866  182551   
15934   chrX  70341930     rs1199457   T   G   10828  0.0613596  176468   
15935   chrX  70926625     rs6525447   G   C   36218   0.238416  151911   
15936   chrX  72140250     rs7061150   C   T   12196  0.0674621  180783   
15937   chrY   6246522   rs201475959   A   G    1025  0.0780952   13125   
15938   chrY  12720687     rs7067496   G   T    6033  0.0894759   67426   
15939   chrY  22180292  rs1478920645   G   T       1   0.142857       7   
15940   chrY  22406127  rs1195699969   C   A       9          1       9   

          QD variant_type                                                vep  \
0      13.47        mixed

In [31]:
!pwd

/ibex/scratch/penaguka/VAP/thesis
